# 1. Traitement des résultats du Kmeans

**11 mai 2021** : on utilise la version 2 de la base finale, donc la version 3 des modèles.

**Qu'est-ce qui change ?** Après la version 2 (en date du 08/05/21), on généralise encore la fonction qui construit l'indicatrice sommaire : on parcourt les différents mots du début du sommaire, on lâche un peu de mou dans la sélection du sommaire, on sélectionne brutalement les 200 lignes après l'apparition du mot débutant le sommaire si besoin etc... Bon, même la détection de l'apparition est sujette à caution : parfois, les indices semblent lointains. C'est pourquoi on a rajouter une restriction. Si l'indice du sommaire (c'est-à-dire le numéro de la ligne où débuterait le sommaire) est trop élevé (et que l'on a toujours pas de sommaire pour l'étude), on ne prend pas de sommaire et on accepte (pour le moment) de laisser cette étude vide finalement. Cette restriction est basée sur l'indice moyen des études ayant un sommaire correct en bout de pipeline, qui est de 44, pour être moins rigide nous avons fixé ce seuil à 100. De même parfois, les indicatrices sommaires sont trop petites, donc si en première approche il y a moins de 50 lignes indiquées, on poursuit avec la nouvelle approche.
En soi, on pourrait justement dire que le sommaire se trouve probablement dans le 400 premières lignes (par exemple) et ainsi prendre encore plus brutalement ces lignes, mais cela reste à discuter.

In [1]:
# -*- coding: utf-8 -*-
import pandas as pd, numpy as np
from bs4 import BeautifulSoup
import time
from unidecode import unidecode
import re
import pickle

chemin="C:/Users/theo.roudil-valentin/Documents/Donnees/DSS/sommaire"
base_finale=pickle.load(open(chemin+"/base_pour_Bagging_final_4.pickle",'rb'))
base_finale
print('Il y a ',len(np.unique(base_finale.num_etude)),"études")

Il y a  148 études


In [2]:
base_finale

phrase  num_etude  \
0                          <title>EI Munchhouse_V3</title>    1003691   
1        <h1><a name="bookmark0"></a><span class="font2...    1003691   
2        <p><span class="font20" style="font-weight:bol...    1003691   
3        <p><span class="font14">Agence Aquitaine</span...    1003691   
4                <p><span class="font14">SAFEGE</span></p>    1003691   
...                                                    ...        ...   
2443029  <span class="font21">Disponible sur le site de...     238301   
2443030  <a href="http://www.clefdeschamps.info/"><span...     238301   
2443031  <p><sup><a href="#footnote14">14</a></sup><a n...     238301   
2443032  <span class="font0" style="font-weight:bold;">...     238301   
2443033  <span class="font21">ANSES, 2011. Dispositifs ...     238301   

                                                  phrase_2         0  \
0                                         EI Munchhouse_V3  0.000000   
1                                                       06  0.048998   
2                                                     2019  0.022272   
3                                         Agence Aquitaine  0.001114   
4                                                   SAFEGE  0.001114   
...                                                    ...       ...   
2443029  Disponible sur le site de Réseau de Transport ...  0.001114   
2443030                     http://www.clefdeschamps.info/  0.001114   
2443031                                                 14  0.000000   
2443032                                                     0.001114   
2443033  ANSES, 2011. Dispositifs d’exploitation d’éner...  0.010022   

         ventre_0  ventre_1  ventre_2  ventre_3  ventre_4  ventre_5  ...   38  \
0        0.007237  0.001262  0.209389  0.139448  0.353363  0.130169  ...  0.0   
1        0.021633  0.027711  0.201385  0.156727  0.325818  0.098187  ...  0.0   
2        0.011876  0.013931  0.204308  0.128357  0.321930  0.092321  ...  0.0   
3        0.011479  0.006782  0.209288  0.135008  0.264427  0.141187  ...  0.0   
4        0.007209  0.006764  0.206694  0.135066  0.262446  0.141680  ...  0.0   
...           ...       ...       ...       ...       ...       ...  ...  ...   
2443029  0.032353  0.004729  0.199404  0.144911  0.247463  0.130676  ...  0.0   
2443030  0.025438  0.017394  0.223514  0.165179  0.301570  0.149461  ...  0.0   
2443031  0.013150  0.016671  0.202500  0.140741  0.379011  0.158092  ...  0.0   
2443032  0.011273  0.014694  0.197234  0.152133  0.226744  0.088159  ...  0.0   
2443033  0.068598  0.004946  0.228507  0.137549  0.358905  0.125026  ...  0.0   

          39    f_mots   f_carac  html_carac  ind_sommaire  sommaire_longueur  \
0        0.0  0.002841  0.006463    0.005215           0.0                0.0   
1        0.0  0.000000  0.000431    0.027724           0.0                0.0   
2        0.0  0.000000  0.001293    0.014548           0.0                0.0   
3        0.0  0.002841  0.006463    0.010705           0.0                0.0   
4        0.0  0.000000  0.002154    0.007960           0.0                0.0   
...      ...       ...       ...         ...           ...                ...   
2443029  0.0  0.031250  0.028867    0.023058           0.0                0.0   
2443030  0.0  0.000000  0.012495    0.024979           0.0                0.0   
2443031  0.0  0.000000  0.000431    0.016744           0.0                0.0   
2443032  0.0  0.002841  0.000000    0.014548           0.0                0.0   
2443033  0.0  0.051136  0.065489    0.046390           0.0                0.0   

         sommaire_int  caractere_spec  label_k_4  
0                 0.0             0.0          0  
1                 0.0             0.0          0  
2                 0.0             0.0          0  
3                 0.0             0.0          0  
4                 0.0             0.0          0  
...               ...             ...        ...  
2443029

Attention à bien vérifier la correspondance des labels du Kmeans !!

## 1.1 Vérification des labelisés 1 par le Kmeans

**ATTENTION** Pour la version 3, les labels Kmeans sont inversés !

In [4]:
N=10000

for i in base_finale[base_finale.label_k_4==1].iloc[:N,:].index:
    print("Indice :",i,"\n",base_finale.phrase_2[i])

Indice : 28 
 
V0
Indice : 29 
 
Lucie CHABOT
Indice : 30 
 
06/06/19
Indice : 31 
 
Version initiale
Indice : 32 
 
V1
Indice : 33 
 
Lucie CHABOT
Indice : 34 
 
10/06/19
Indice : 35 
 
Intégration remarques Olivier Million
Indice : 36 
 
V2
Indice : 37 
 
Lucie CHABOT
Indice : 38 
 
13/06/19
Indice : 39 
 
Intégration remarques ENGIE
Indice : 40 
 
V3
Indice : 41 
 
Lucie CHABOT
Indice : 42 
 
14/06/19
Indice : 43 
 
Intégration remarques ENGIE
Indice : 251 
 
Lieu dit / adresse
Indice : 253 
 
Surface du site actuel
Indice : 254 
 
26,5 ha
Indice : 259 
 
Section et parcelles concernées
Indice : 271 
 
Terrain
Indice : 277 
 
Spécificités techniques
Indice : 285 
 
Production et Équivalent en termes de personnes alimentées
Indice : 286 
 
Une production d’énergie annuelle estimée à 16 048 MWh/an Équivalent en termes de personnes : 7 300 personnes alimentées
Indice : 287 
 
Quantité de CO2 évitée
Indice : 296 
 
Climat
Indice : 299 
 
Aucun
Indice : 300 
 
Topographie
Indice : 302 
 

Bon sur l'échantillon de 1000, les labelisés 1 semblent être tous des "non-titres", donc c'est super !

## 1.2 Vérification des labelisés 0 par le Kmeans
### 1.2.1 Essai sur sous-ensemble

In [5]:
N=0#10000

for i in base_finale[base_finale.ind_sommaire==1][base_finale.label_k_4==0].iloc[N:N+10000,:].index:
    print("Indice :",i,"\n",base_finale.phrase_2[i])

c:\Users\theo.roudil-valentin\venv\lib\site-packages\ipykernel_launcher.py:3: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  This is separate from the ipykernel package so we can avoid doing imports until
Indice : 44 
 Sommaire
Indice : 45 
 
1.Résumé non technique
Indice : 46 
 
1.1 Présentation synthétique du projet 
Indice : 47 
 
1.2 Synthèse de l’état initial 
Indice : 48 
 
1.3 Synthèse des impacts et des mesures associées 
Indice : 49 
 
2.Présentation du demandeur 
Indice : 50 
 
2.1 Présentation générale d’ENGIE
Indice : 51 
 
2.2 ENGIE Green : un leader des énergies renouvelables en France 
Indice : 52 
 
2.3 Le solaire avec ENGIE Green 
Indice : 53 
 
2.4 Contacts
Indice : 54 
 
3.Description du projet 
Indice : 55 
 
3.1 Localisation du projet
Indice : 56 
 
3.2 Nature et objet de l’opération 
Indice : 57 
 
3.3 Généralités - Principe de base du photovoltaïque
Indice : 58 
 
3.4 Présentation des installations projetées
Indice : 59 
 
3.5 Trava

In [108]:
base=base_finale.iloc[:296183,:]
c=[1 if (base.ind_sommaire[i]==1) and (base.label_k_3[i]==1) else 0 for i in base.index]
#print(len(c))
c_index=[i for i in base.index if base.phrase_2[i]=='^' or base.phrase_2[i]==base.iloc[141175,:].phrase_2]
for i in c_index:
    c[i]=0
#print(len(c))
c[29533:29584]=np.zeros(29584-29533)
#print(len(c))
c[29901:131462]=np.zeros(131462-29901)
#print(len(c))
c[141223:162733]=np.zeros(162733-141223)
#print(len(c))
#c[162550:162535]=np.zeros(162535-162550)
c[177975:186252]=np.zeros(186252-177975)
#print(len(c))
c[203924:247583]=np.zeros(247583-203924)
#print(len(c))
c[284870:285811]=np.zeros(285811-284870)
#print(len(c))
c[285860:296183]=np.zeros(296183-285860)
#print(len(c))
base['label']=c
base

296183
296183
296183
296183


In [111]:
#c_index
#base[base.phrase_2==base.iloc[141175,:].phrase_2]
base.label.sum()/base.shape[0]*100

1.315402977213412

In [0]:
base[base.label==1]

In [0]:
for i in base[base.label==1].index:
    print("Indice :",i,"\n",base.phrase_2[i])

Désormais, on a une nouvelle variable : label.

Elle est le croisement de indicatrice_sommaire et label_k puis passe dans un nouveau nettoyage. On peut donc donner les anciennes variables utilisées pour construire notre nouvel algorithme.

In [112]:
base.iloc[:,3:-1]

0  ventre_0  ventre_1  ventre_2  ventre_3  ventre_4  ventre_5  ventre_6  ventre_7  ventre_8  ventre_9  ventre_10  ventre_11   33   34   35   36   37   38   39    f_mots   f_carac  html_carac  ind_sommaire  sommaire_longueur  sommaire_int  caractere_spec  label_k_3
0       0.000000  0.903363  0.215909  0.521686  0.749125  0.022868  0.425675  0.689352  0.760611  0.452229  0.296891   0.228436   0.247048  0.0  1.0  0.0  0.0  0.0  0.0  0.0  0.002841  0.006463    0.005215           0.0                0.0           0.0             0.0          1
1       0.187234  0.523014  0.614289  0.882017  0.610726  0.101309  0.347138  0.444512  0.318033  0.411697  0.300860   0.137647   0.268558  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.000431    0.027724           0.0                0.0           0.0             0.0          1
2       0.085106  0.337854  0.495530  0.732244  0.263894  0.180661  0.230749  0.476202  0.353159  0.518603  0.227985   0.127242   0.273854  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.001293    0.014548           0.0                0.0           0.0             0.0          1
3       0.004255  0.767331  0.441971  0.045072  0.304002  0.185098  0.272320  0.501349  0.361487  0.383894  0.255841   0.201873   0.249672  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.002841  0.006463    0.010705           0.0                0.0           0.0             0.0          1
4       0.004255  0.767331  0.441971  0.045072  0.304002  0.185098  0.272320  0.501349  0.361487  0.383894  0.255841   0.201873   0.249672  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.002154    0.007960           0.0                0.0           0.0             0.0          1
...          ...       ...       ...       ...       ...       ...       ...       ...       ...       ...       ...        ...        ...  ...  ...  ...  ...  ...  ...  ...       ...       ...         ...           ...                ...           ...             ...        ...
296178  0.004255  0.790612  0.409500  0.078011  0.209536  0.309651  0.402867  0.289109  0.583797  0.230445  0.298113   0.291061   0.218952  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.019886  0.019388    0.021136           1.0                0.0           0.0             1.0          1
296179  0.004255  0.790612  0.409500  0.078011  0.209536  0.309651  0.402867  0.289109  0.583797  0.230445  0.298113   0.291061   0.218952  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.048295  0.044808    0.037332           1.0                0.0           0.0             1.0          1
296180  0.004255  0.419483  0.819485  0.423600  0.218639  0.215679  0.278888  0.479132  0.375938  0.520773  0.237621   0.112565   0.268572  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.008523  0.010340    0.034312           1.0                0.0           0.0             0.0          1
296181  0.004255  0.767331  0.441971  0.045072  0.304002  0.185098  0.272320  0.501349  0.361487  0.383894  0.255841   0.201873   0.249672  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.056818  0.056010    0.041998           1.0                0.0           0.0             0.0          1
296182  0.004255  0.419483  0.819485  0.423600  0.218639  0.215679  0.278888  0.479132  0.375938  0.520773  0.237621   0.112565   0.268572  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.019886  0.021112    0.026901           1.0                0.0           0.0             0.0          1

[296183 rows x 28 columns]

# 2. Classification supervisée

Attention, désormais, titres ==1 et non_titres==0

In [113]:
from sklearn.model_selection import train_test_split
X_train,X_test,y_train,y_test=train_test_split(base.iloc[:,3:-1],base.loc[:,'label'],test_size=0.25)

In [114]:
print("Train : proportion de 1 :",round(y_train.sum()/len(y_train)*100,1)," ; de 0 :",round((1-y_train.sum()/len(y_train))*100,1))
print("Test : proportion de 1 :",round(y_test.sum()/len(y_test)*100,1)," ; de 0 :",round((1-y_test.sum()/len(y_test))*100,1))

Train : proportion de 1 : 1.3  ; de 0 : 98.7
Test : proportion de 1 : 1.3  ; de 0 : 98.7


### Arbre de décision

In [0]:
k=0 # On a plus besoin d'étudier le k
X_train_2=X_train.iloc[:,:(X_train.shape[1]-k)]
X_test_2=X_test.iloc[:,:(X_train.shape[1]-k)]

from sklearn.tree import DecisionTreeClassifier
DTC = DecisionTreeClassifier(class_weight="balanced")
DTC.fit(X_train_2, y_train)

print("Score train :",round(DTC.score(X_train_2,y_train),3))
print("Score test :",round(DTC.score(X_test_2,y_test),3))

from sklearn.metrics import confusion_matrix
confusion_matrix(y_test,DTC.predict(X_test_2))

In [0]:
#print("La variable",X_train_2.columns[-1],"permet d'atteindre un score de 1.")

In [0]:
#np.corrcoef(X_train_2.iloc[:,X_train_2.columns[-1]],y_train)

### Forêt aléatoire

In [0]:
################ NE PAS LANCER !
######## De même, plus besoin d'étudier cela, je laisse pour l'historique du travail
absi=[]
ordo=[]
ordo_test=[]

for i in range(1,X_train.shape[1]):
    X_train_2=X_train.iloc[:,:i]
    X_test_2=X_test.iloc[:,:i]

    DTC = RandomForestClassifier(n_estimators=10,verbose=0,class_weight="balanced")
    DTC.fit(X_train_2, y_train)

    ordo.append(DTC.score(X_train_2,y_train))
    ordo_test.append(DTC.score(X_test_2,y_test))
    absi.append(i)

import matplotlib.pyplot as plt
f,a=plt.subplots(1,figsize=(12,6))
a.plot(absi,ordo)
a.plot(absi,ordo_test)
a.set(xlabel="Nombre de variables",ylabel='Score',
      title='Score de la random forest en fonction du nombre de variables')
plt.legend(['train','test'])

In [0]:
############## On passe aux forêts :
n=10 # On essaie avec 10 estimateurs

from sklearn.ensemble import RandomForestClassifier
RFC = RandomForestClassifier(n_estimators=n,verbose=0,class_weight="balanced")
RFC.fit(X_train, y_train)

print("Score train :",round(RFC.score(X_train,y_train),3))
print("Score test :",round(RFC.score(X_test,y_test),3))

from sklearn.metrics import confusion_matrix
print("Matrice de confusion sur le train \n",confusion_matrix(y_train,RFC.predict(X_train)))
print("Matrice de confusion sur le test \n",confusion_matrix(y_test,RFC.predict(X_test)))

On fait encore des erreurs, donc on poursuit, on augmente n

In [170]:
n=100 # On essaie avec 100 estimateurs

from sklearn.ensemble import RandomForestClassifier
RFC = RandomForestClassifier(n_estimators=n,verbose=0,class_weight="balanced")
RFC.fit(X_train, y_train)

print("Score train :",round(RFC.score(X_train,y_train),3))
print("Score test :",round(RFC.score(X_test,y_test),3))

from sklearn.metrics import confusion_matrix
print("Matrice de confusion sur le train \n",confusion_matrix(y_train,RFC.predict(X_train)))
print("Matrice de confusion sur le test \n",confusion_matrix(y_test,RFC.predict(X_test)))

Score train : 0.999
Score test : 0.998
Matrice de confusion sur le train 
 [[218920    293]
 [     5   2919]]
Matrice de confusion sur le test 
 [[72950   124]
 [   37   935]]


In [175]:
RFC.feature_importances_*100

array([1.75777010e+00, 4.52853721e+00, 2.11577728e+00, 4.88418372e+00,
       2.32417199e+00, 6.94486316e+00, 7.35113304e+00, 1.20265047e+00,
       1.66884328e+01, 1.34508540e+00, 1.96580708e+00, 2.45725515e+00,
       8.62825227e-01, 9.57753958e-02, 6.24381656e-13, 5.47975668e-02,
       1.53468014e-02, 4.54545147e-02, 5.73335595e-01, 2.43626692e-02,
       1.48430819e+00, 1.99237601e+00, 2.41255173e+00, 3.74102584e+01,
       9.45064264e-01, 8.42558452e-02, 7.07615547e-02, 3.62858832e-01])

Malgré la multiplication par 10 du nombre d'estimateurs, on ne réussit pas à classifier parfaitement. Poursuivons.

### Forêt aléatoire et bagging

On va faire 100 fois la sélection du meilleur estimateur parmi 100 forêt aléatoire estimée.

In [115]:
from sklearn.ensemble import BaggingClassifier

RFC = RandomForestClassifier(n_estimators=100,verbose=0,class_weight="balanced")#,bootstrap=False) #à voir
Bagging = BaggingClassifier(RFC,n_estimators=100,verbose=0)
Bagging.fit(X_train, y_train)

BaggingClassifier(base_estimator=RandomForestClassifier(class_weight='balanced'),
                  n_estimators=100)

In [116]:
print("Score train :",round(Bagging.score(X_train,y_train),3))
print("Score test :",round(Bagging.score(X_test,y_test),3))

from sklearn.metrics import confusion_matrix
print("Matrice de confusion sur le train \n",confusion_matrix(y_train,Bagging.predict(X_train)))
print("Matrice de confusion sur le test \n",confusion_matrix(y_test,Bagging.predict(X_test)))

Score train : 0.999
Score test : 0.998
Matrice de confusion sur le train 
 [[218954    259]
 [    70   2854]]
Matrice de confusion sur le test 
 [[72964   110]
 [   45   927]]


Malgré le Bagging, on ne réussit pas à classer **parfaitement**.

In [120]:
base['label_rf']=Bagging.predict(base.iloc[:,3:-1])

/data/dataiku/data_dir_design/code-envs/python/THEO_/lib/python3.6/site-packages/ipykernel_launcher.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  """Entry point for launching an IPython kernel.


In [122]:
for i in base[base.label_rf==1].phrase_2:
    print(i)

Sommaire

1.Résumé non technique

1.1 Présentation synthétique du projet 

1.2 Synthèse de l’état initial 

1.3 Synthèse des impacts et des mesures associées 

2.Présentation du demandeur 

2.1 Présentation générale d’ENGIE

2.2 ENGIE Green : un leader des énergies renouvelables en France 

2.3 Le solaire avec ENGIE Green 

2.4 Contacts

3.Description du projet 

3.1 Localisation du projet

3.2 Nature et objet de l’opération 

3.3 Généralités - Principe de base du photovoltaïque

3.4 Présentation des installations projetées

3.5 Travaux en vue de l’implantation des panneaux photovoltaïques

3.6 Mise en place d’un « chantier propre » 

3.7 Appréciation sommaire des dépenses 

3.8 Synthèse des caractéristiques générales et technique du projet 

3.9 Réglementation applicable 

4.Démantèlement et remise en état du site 

4.1 Devenir du site en fin de vie des modules 

4.2 Recyclage et valorisation des éléments

4.3 Remise en état des terrains 

5.Justification du choix d’aménagement et sol


Figure 15 : Ordre de grandeurs des limites réglementaires d’exposition en mSv/an ajoutes

Figure 16 : Plan des servitudes

Figure 17 : carte du relief autour du site

Figure 18 : Températures moyennes mensuelles en °C à Limoges-bellegarde

Figure 19 : Hauteurs de précipitations mensuelles moyennes (en mm) a limoges-bellegarde

Figure 20 : Nombre d’heures d’ensoleillement à Limoges-Bellegarde

Figure 21 : Contexte géologiques du site

Figure 22 : Piézométrie de la nappe des Arènes

Figure 23 : Localisation des points d’eau

Figure 24 : Concentrations moyennes mesurées en uranium, radium et chlorures pour les piézomètres courts (nappe des arènes) situés autour du stockage (2012)

Figure 25 : Concentrations moyennes mesurées en sulfates pour les piézomètres courts (nappe des arènes) situés autour du stockage (2012)

Figure 26 : Contexte hydrogéologique du site du Bernardan

Figure 27 : Hydrogramme moyen sur 33 ans sur La Benaize

Figure 28 : Contexte hydrographique

Figure 29 : Extrait d

Carte 12 : Risque de non-atteinte de bon état quantitatif pour les masses d'eau souterraines affleurantes
(Etat des lieux 2013)
Carte 13 : Risque de non-atteinte du bon état chimique des masses d'eau souterraines affleurantes...37
Carte 14 : Localisation des ruisseaux autour du projet
Carte 15 : Etat chimique des masses d'eau superficielles (Etat des lieux 2013)
Carte 16 : Etat écologique des masses d'eau superficielles (Etat des lieux 2013)
Carte 17 : Risque de non-atteinte de bon état écologique des masses d'eau superficielles
Carte 18 : Risque de non-atteinte de bon état chimique des masses d'eau superficielles
Carte 19 : Localisation des mouvements de terrain dans le Sud de la Charente-Maritime
Carte 20 : Aléa du risque de retrait-gonflement des argiles
Carte 21 : AZI à proximité du projet
Carte 22 : Sites industriels BASIAS, ICPE et SEVESO à proximité du projet
Carte 23 : Zone de 500 m autour des éoliennes du projet
Carte 24 : Lieux-dits voisins du projet
Carte 25 : Distance entre

rojet avec la charte du
7.4
 C
ompatibilite du 
P
rojet avec le 
P
lan departemental de l
’H
ABITAT
 
7.5
 C
ompatibilite du projet avec le
 SDAGE 
L
oire 
B
retagne
7.6
 C
ompatibilite du projet avec le

8. MESURES PREVUES POUR EVITER, REDUIRE OU COMPENSER LES EFFETS NEGATIFS - ESTIMATION
DE LEUR COUT - EFFETS ATTENDUS ET SUIVI DE LEURS EFFETS
8.1
 M
esures liees aux periodes de chantier
 

8.1.1 Mesures relatives aux usagers et riverains 

8.1.2 Mesures liées au cadre physique 

8.1.3 Mesures liées au cadre biologique 

8.1.4 Mesures liées au cadre paysager 

8.1.5 Mesures liées au cadre patrimonial 

8.1.6 Mesures liées à la qualité de l’air
8.2
 M
esures prevues pour eviter
, 
reduire ou compenser les effets negatifs permanents
 

8.2.1 Mesures liées au cadre physique 

8.2.2 Prise en compte des risques majeurs 

8.2.3 Mesures liées au cadre biologique et écologique 

8.2.4 Mesures liées au cadre paysager 
3

8.2.5 Mesures liées au cadre patrimonial 

8.2.6 Mesures liées au cadre h

1.2.2 Résultats

1.2.3 Enjeux.
1.3

1.3.1 Résultats

1.3.2 Enjeux.
1.4
 Avifaune migratrice postnuptiale

1.4.1 Méthodologie

1.4.2 Résultats

1.4.3 Enjeux.
1.5
 Avifaune hivernante

1.5.1 Méthodologie

1.5.2 Résultats

1.5.3 Enjeux.
1.6
 Avifaune migratrice prénuptiale

1.6.1 Méthodologie

1.6.2 Résultats

1.6.3 Enjeux.
1.7
 SYNTHESE DES MIGRATIONS
1.8

1.8.1 Méthodologie

1.8.2 Résultats

1.8.3 Espèces remarquables

1.8.4 Habitats d'espèces

1.8.5 Enjeux.
1.9
 Milan royal

1.9.1 Méthodologie

1.9.2 Résultats

1.9.3 Enjeux.
1.10
 Busards

1.10.1 Méthodologie

1.10.2 Résultats

1.10.3 Enjeux.
1.11
87
93
95

1.11.2 Résultats.......................................

1.11.3 Espèce patrimoniale.................

1.11.5 Enjeux.
1.12

1.12.1 Méthodologie

1.12.2 Résultats

1.12.3 Espèces patrimoniales

1.12.4 Enjeux.
1.13

1.13.1 Méthodologie

1.13.2 Résultats

1.13.3 Enjeux.
1.14
 Continuités écologiques

1.14.1 Au niveau national

1.14.2 Au niveau régional

1.14.3 Au niveau local

2 DEFINIT

In [123]:
(base.label_rf.sum()/len(base))*100

1.4011607688489884

In [124]:
base

phrase  num_etude                                           phrase_2         0  ventre_0  ventre_1  ventre_2  ventre_3  ventre_4  ventre_5  ventre_6  ventre_7  ventre_8  ventre_9  ventre_10  ventre_11   33   34   35   36   37   38   39    f_mots   f_carac  html_carac  ind_sommaire  sommaire_longueur  sommaire_int  caractere_spec  label_k_3  label  label_rf
0                         <title>EI Munchhouse_V3</title>    1003691                                   EI Munchhouse_V3  0.000000  0.903363  0.215909  0.521686  0.749125  0.022868  0.425675  0.689352  0.760611  0.452229  0.296891   0.228436   0.247048  0.0  1.0  0.0  0.0  0.0  0.0  0.0  0.002841  0.006463    0.005215           0.0                0.0           0.0             0.0          1    0.0       0.0
1       <h1><a name="bookmark0"></a><span class="font2...    1003691                                                 06  0.187234  0.523014  0.614289  0.882017  0.610726  0.101309  0.347138  0.444512  0.318033  0.411697  0.300860   0.137647   0.268558  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.000431    0.027724           0.0                0.0           0.0             0.0          1    0.0       0.0
2       <p><span class="font20" style="font-weight:bol...    1003691                                               2019  0.085106  0.337854  0.495530  0.732244  0.263894  0.180661  0.230749  0.476202  0.353159  0.518603  0.227985   0.127242   0.273854  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.001293    0.014548           0.0                0.0           0.0             0.0          1    0.0       0.0
3       <p><span class="font14">Agence Aquitaine</span...    1003691                                   Agence Aquitaine  0.004255  0.767331  0.441971  0.045072  0.304002  0.185098  0.272320  0.501349  0.361487  0.383894  0.255841   0.201873   0.249672  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.002841  0.006463    0.010705           0.0                0.0           0.0             0.0          1    0.0       0.0
4               <p><span class="font14">SAFEGE</span></p>    1003691                                             SAFEGE  0.004255  0.767331  0.441971  0.045072  0.304002  0.185098  0.272320  0.501349  0.361487  0.383894  0.255841   0.201873   0.249672  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.002154    0.007960           0.0                0.0           0.0             0.0          1    0.0       0.0
...                                                   ...        ...                                                ...       ...       ...       ...       ...       ...       ...       ...       ...       ...       ...       ...        ...        ...  ...  ...  ...  ...  ...  ...  ...       ...       ...         ...           ...                ...           ...             ...        ...    ...       ...
296178  <li>\n<p><span class="font6">■ Les aléas d’acc...     106905    \n■ Les aléas d’accumulation de gaz dangereux ;  0.004255  0.790612  0.409500  0.078011  0.209536  0.309651  0.402867  0.289109  0.583797  0.230445  0.298113   0.291061   0.218952  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.019886  0.019388    0.021136           1.0                0.0           0.0             1.0          1    0.0       0.0
296179  <li>\n<p><span class="font6">■ Les aléas d’ino...     106905  \n■ Les aléas d’inondation localisée ou de rem...  0.004255  0.790612  0.409500  0.078011  0.209536  0.309651  0.402867  0.289109  0.583797  0.230445  0.298113   0.291061   0.218952  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.048295  0.044808    0.037332           1.0                0.0           0.0             1.0          1    0.0       0.0
296180  <p><a name="bookmark921"></a><span class="font...     106905                          Sur le territoire d’étude  0.004255  0.419483  0.819485  0.423600  0.218639  0.215679  0.278888  0.479132  0.375938  0.520773  0.237621   0.112565   0.268572  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.008523  0.010340    0.034312           1.0                0.0          

On va sauvegarder la base d'entraînement avec son résultat pour reproduction

In [125]:
da=dataiku.Folder('lZ0B3sSL')
import pickle
dico_Bagging={}
dico_Bagging['train']=[X_train,y_train]
dico_Bagging['test']=[X_test,y_test]
dico_Bagging['base']=base
dico_Bagging['modele']=Bagging
pickle.dump(dico_Bagging,open(da.get_path()+"/dico_Bagging_v3.pickle",'wb'))

Vu le travail qu'on a fait de re-labellisation (semi-supervisation) on va sauvegarder ce modèle (et vérifier qu'on l'a bien enregistré en le re-téléchargeant)

In [0]:
#clf_titres_fin=Bagging.copy()
da=dataiku.Folder('lZ0B3sSL')
import pickle
pickle.dump(Bagging,open(da.get_path()+"/Bagging_model_v3.pickle",'wb'))
#da.upload_file("Bagging_model", Bagging)

In [0]:
clf_titres_fin=pickle.load(open(da.get_path()+"/Bagging_model.pickle",'rb'))
print(clf_titres_fin)
clf_titres_fin.predict(base.iloc[:100,3:-2])

# 3. Prédiction supervisée de l'ensemble de notre base

Attention le chargement de la base prend généralement 25 minutes

In [0]:
########### Chargement du modèle
import dataiku
import pandas as pd, numpy as np
from dataiku import pandasutils as pdu
import time
import pickle
da=dataiku.Folder('lZ0B3sSL')
dico=pickle.load(open(da.get_path()+"/dico_Bagging_v3.pickle",'rb'))
clf_titres_fin=dico['modele']

In [126]:
base_finale=pickle.load(open(da.get_path()+"/base_pour_Bagging_final_v3.pickle",'rb'))

In [127]:
base_finale

phrase  num_etude                                           phrase_2         0  ventre_0  ventre_1  ventre_2  ventre_3  ventre_4  ventre_5  ventre_6  ventre_7  ventre_8  ventre_9  ventre_10  ventre_11   33   34   35   36   37   38   39    f_mots   f_carac  html_carac  ind_sommaire  sommaire_longueur  sommaire_int  caractere_spec  label_k_3
0                          <title>EI Munchhouse_V3</title>    1003691                                   EI Munchhouse_V3  0.000000  0.903363  0.215909  0.521686  0.749125  0.022868  0.425675  0.689352  0.760611  0.452229  0.296891   0.228436   0.247048  0.0  1.0  0.0  0.0  0.0  0.0  0.0  0.002841  0.006463    0.005215           0.0                0.0           0.0             0.0          1
1        <h1><a name="bookmark0"></a><span class="font2...    1003691                                                 06  0.187234  0.523014  0.614289  0.882017  0.610726  0.101309  0.347138  0.444512  0.318033  0.411697  0.300860   0.137647   0.268558  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.000431    0.027724           0.0                0.0           0.0             0.0          1
2        <p><span class="font20" style="font-weight:bol...    1003691                                               2019  0.085106  0.337854  0.495530  0.732244  0.263894  0.180661  0.230749  0.476202  0.353159  0.518603  0.227985   0.127242   0.273854  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.001293    0.014548           0.0                0.0           0.0             0.0          1
3        <p><span class="font14">Agence Aquitaine</span...    1003691                                   Agence Aquitaine  0.004255  0.767331  0.441971  0.045072  0.304002  0.185098  0.272320  0.501349  0.361487  0.383894  0.255841   0.201873   0.249672  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.002841  0.006463    0.010705           0.0                0.0           0.0             0.0          1
4                <p><span class="font14">SAFEGE</span></p>    1003691                                             SAFEGE  0.004255  0.767331  0.441971  0.045072  0.304002  0.185098  0.272320  0.501349  0.361487  0.383894  0.255841   0.201873   0.249672  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.002154    0.007960           0.0                0.0           0.0             0.0          1
...                                                    ...        ...                                                ...       ...       ...       ...       ...       ...       ...       ...       ...       ...       ...       ...        ...        ...  ...  ...  ...  ...  ...  ...  ...       ...       ...         ...           ...                ...           ...             ...        ...
2443029  <span class="font21">Disponible sur le site de...     238301  Disponible sur le site de Réseau de Transport ...  0.004255  0.952355  0.560512  0.194462  0.650605  0.105932  0.388558  0.470029  0.326538  0.276844  0.327395   0.212637   0.244277  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.031250  0.028867    0.023058           0.0                0.0           0.0             0.0          1
2443030  <a href="http://www.clefdeschamps.info/"><span...     238301                     http://www.clefdeschamps.info/  0.004255  0.980319  0.503047  0.241811  0.570262  0.317373  0.758813  0.622318  0.129463  0.341865  0.353711   0.167576   0.254206  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.012495    0.024979           0.0                0.0           0.0             0.0          1
2443031  <p><sup><a href="#footnote14">14</a></sup><a n...     238301                                                 14  0.000000  0.761311  0.029575  0.430819  0.347951  0.290608  0.719598  0.978864  0.815095  0.711131  0.240078   0.170334   0.262575  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.000431    0.016744           0.0                0.0           0.0             0.0          1
2443032  <span class="font0" style="font-weight:bold;">...     238301                                           

Attention à bien laisser la dernière variable de la grosse base puisque le modèle utilise label_k pour prédire label

In [128]:
start=time.time()
pred=Bagging.predict(base_finale.iloc[:,3:])
end=time.time()
print("Durée de la prédiction :",round((end-start)/60,2),"minutes")

Durée de la prédiction : 32.11 minutes


In [0]:
pred.shape,base_finale.shape

In [129]:
base_finale['label_RF']=pred

In [0]:
base_finale.label_RF.sum()/len(base_finale)*100

In [0]:
for i in base_finale[base_finale.label_RF==1].iloc[:,:].phrase_2:
    print(i)

In [130]:
da=dataiku.Folder('lZ0B3sSL')
import pickle
pickle.dump(base_finale.loc[:,['num_etude','phrase_2','label_RF']],open(da.get_path()+"/label_RF_3.pickle",'wb'))

In [0]:
base_classif_RF_df = base_finale
base_classif_RF = dataiku.Dataset("base_classif_RF")
base_classif_RF.write_with_schema(base_classif_RF_df)

In [117]:
base_finale

phrase  num_etude                                           phrase_2         0  ventre_0  ventre_1  ventre_2  ventre_3  ventre_4  ventre_5  ventre_6  ventre_7  ventre_8  ventre_9  ventre_10  ventre_11   33   34   35   36   37   38   39    f_mots   f_carac  html_carac  ind_sommaire  sommaire_longueur  sommaire_int  caractere_spec  label_k_3
0                          <title>EI Munchhouse_V3</title>    1003691                                   EI Munchhouse_V3  0.000000  0.903363  0.215909  0.521686  0.749125  0.022868  0.425675  0.689352  0.760611  0.452229  0.296891   0.228436   0.247048  0.0  1.0  0.0  0.0  0.0  0.0  0.0  0.002841  0.006463    0.005215           0.0                0.0           0.0             0.0          1
1        <h1><a name="bookmark0"></a><span class="font2...    1003691                                                 06  0.187234  0.523014  0.614289  0.882017  0.610726  0.101309  0.347138  0.444512  0.318033  0.411697  0.300860   0.137647   0.268558  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.000431    0.027724           0.0                0.0           0.0             0.0          1
2        <p><span class="font20" style="font-weight:bol...    1003691                                               2019  0.085106  0.337854  0.495530  0.732244  0.263894  0.180661  0.230749  0.476202  0.353159  0.518603  0.227985   0.127242   0.273854  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.001293    0.014548           0.0                0.0           0.0             0.0          1
3        <p><span class="font14">Agence Aquitaine</span...    1003691                                   Agence Aquitaine  0.004255  0.767331  0.441971  0.045072  0.304002  0.185098  0.272320  0.501349  0.361487  0.383894  0.255841   0.201873   0.249672  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.002841  0.006463    0.010705           0.0                0.0           0.0             0.0          1
4                <p><span class="font14">SAFEGE</span></p>    1003691                                             SAFEGE  0.004255  0.767331  0.441971  0.045072  0.304002  0.185098  0.272320  0.501349  0.361487  0.383894  0.255841   0.201873   0.249672  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.002154    0.007960           0.0                0.0           0.0             0.0          1
...                                                    ...        ...                                                ...       ...       ...       ...       ...       ...       ...       ...       ...       ...       ...       ...        ...        ...  ...  ...  ...  ...  ...  ...  ...       ...       ...         ...           ...                ...           ...             ...        ...
2443029  <span class="font21">Disponible sur le site de...     238301  Disponible sur le site de Réseau de Transport ...  0.004255  0.952355  0.560512  0.194462  0.650605  0.105932  0.388558  0.470029  0.326538  0.276844  0.327395   0.212637   0.244277  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.031250  0.028867    0.023058           0.0                0.0           0.0             0.0          1
2443030  <a href="http://www.clefdeschamps.info/"><span...     238301                     http://www.clefdeschamps.info/  0.004255  0.980319  0.503047  0.241811  0.570262  0.317373  0.758813  0.622318  0.129463  0.341865  0.353711   0.167576   0.254206  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.012495    0.024979           0.0                0.0           0.0             0.0          1
2443031  <p><sup><a href="#footnote14">14</a></sup><a n...     238301                                                 14  0.000000  0.761311  0.029575  0.430819  0.347951  0.290608  0.719598  0.978864  0.815095  0.711131  0.240078   0.170334   0.262575  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.000431    0.016744           0.0                0.0           0.0             0.0          1
2443032  <span class="font0" style="font-weight:bold;">...     238301                                           

# 4. Active learning
## 4.1 Première boucle

In [156]:
N=300000
train_active=base_finale.iloc[base.shape[0]:base.shape[0]+N,:]

In [166]:
train_active

phrase  num_etude                                           phrase_2         0  ventre_0  ventre_1  ventre_2  ventre_3  ventre_4  ventre_5  ventre_6  ventre_7  ventre_8  ventre_9  ventre_10  ventre_11   33   34   35   36   37   38   39    f_mots   f_carac  html_carac  ind_sommaire  sommaire_longueur  sommaire_int  caractere_spec  label_k_3  label_RF
296183  <h6><a name="bookmark923"></a><span class="fon...     106905                          Risque rupture de barrage  0.004255  0.953618  0.562263  0.199909  0.652759  0.106185  0.391722  0.457804  0.335273  0.270279  0.344049   0.202554   0.247555  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.008523  0.010340    0.027999           1.0                0.0           0.0             0.0          1       0.0
296184  <p><a name="bookmark925"></a><span class="font...     106905                                         Définition  0.004255  0.419483  0.819485  0.423600  0.218639  0.215679  0.278888  0.479132  0.375938  0.520773  0.237621   0.112565   0.268572  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.003878    0.030195           1.0                0.0           0.0             0.0          1       0.0
296185  <span class="font6">Un barrage est un ouvrage,...     106905  Un barrage est un ouvrage, le plus souvent art...  0.004255  0.952355  0.560512  0.194462  0.650605  0.105932  0.388558  0.470029  0.326538  0.276844  0.327395   0.212637   0.244277  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.147727  0.152951    0.101839           1.0                1.0           0.0             0.0          1       0.0
296186  <span class="font6" style="font-weight:bold;">...     106905  les ruptures de barrage sont des accidents rar...  0.004255  0.604507  0.938026  0.572990  0.565242  0.136513  0.395126  0.447812  0.340989  0.413722  0.309174   0.123329   0.263178  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.028409  0.026282    0.028273           1.0                0.0           0.0             0.0          1       0.0
296187  <p><a name="bookmark927"></a><span class="font...     106905                        Manifestation de la rupture  0.004255  0.419483  0.819485  0.423600  0.218639  0.215679  0.278888  0.479132  0.375938  0.520773  0.237621   0.112565   0.268572  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.008523  0.011202    0.034861           1.0                0.0           0.0             0.0          1       0.0
...                                                   ...        ...                                                ...       ...       ...       ...       ...       ...       ...       ...       ...       ...       ...       ...        ...        ...  ...  ...  ...  ...  ...  ...  ...       ...       ...         ...           ...                ...           ...             ...        ...       ...
596178  <td rowspan="2" style="vertical-align:middle;"...    1130980                                 \nNom scientifique  0.004255  0.164178  0.557958  0.005263  0.562748  0.209986  0.387602  0.471471  0.390108  0.377766  0.321405   0.216073   0.145992  0.0  0.0  0.0  0.0  0.0  1.0  0.0  0.002841  0.006894    0.025254           0.0                0.0           0.0             0.0          0       0.0
596179  <td rowspan="2" style="vertical-align:middle;"...    1130980                             \nStatut de protection  0.004255  0.164178  0.557958  0.005263  0.562748  0.209986  0.387602  0.471471  0.390108  0.377766  0.321405   0.216073   0.145992  0.0  0.0  0.0  0.0  0.0  1.0  0.0  0.005682  0.008617    0.026352           0.0                0.0           0.0             0.0          0       0.0
596180  <td rowspan="2" style="vertical-align:middle;"...    1130980                               \nStatut Natura 2000  0.034043  0.082548  0.234004  0.313908  0.608004  0.174968  0.339463  0.468541  0.367329  0.375597  0.311770   0.230750   0.151273  0.0  0.0  0.0  0.0  0.0  1.0  0.0  0.005682  0.007755    0.025803           0.0                0.0           0.0             0.0          0       0.0
596181  <td colspan="

In [169]:
train_active.phrase_2.values[1369]

'6 - 2 Estimation des garanties '

In [165]:
for i in train_active.index:
    if train_active.label_RF[i]==1:
        print("\nIndice :",i-base.shape[0])
        print(train_active.loc[i,'phrase_2'])


Indice : 232
Enjeux identifies du territoire

Indice : 257
 : Echelle de couleur des niveaux de sensibilité

Indice : 294
 : 

Indice : 297
 : 

Indice : 300
 

Indice : 302
Avifaune :

Indice : 303
 

Indice : 305
Chiroptères :

Indice : 306
 

Indice : 308
Autre faune :

Indice : 309
 

Indice : 370
 C - V

Indice : 371
ariantes et justification du projet

Indice : 373
1 Contexte politique et énergétique du projet 

Indice : 374

2 Raisons du choix de la zone d’implantation du projet 

Indice : 375
2 - 1 Intégration au Schéma Régional Climat Air Energie 

Indice : 376
2 - 2 Information et concertation 

Indice : 377

3 Scénario de référence et évolution de l’environnement 

Indice : 378
3 - 1  Etat actuel de l’environnement : « Scénario de référence » 

Indice : 379
3 - 2 Evolution de l’environnement en cas de mise en œuvre du projet 

Indice : 380
3 - 3 Evolution probable de l’environnement en l’absence de mise en œuvre du projet _

Indice : 381

4 Description des variantes d’impla


Indice : 12484
Conformité évaluée / arrêté du 26 août 201

Indice : 12553
Au 

Indice : 12632
iMariléef

Indice : 12660
^^Marignê

Indice : 12706
-de-Feiny

Indice : 12713
1

Indice : 12722
1

Indice : 12728
kccileWe'

Indice : 12743
7

Indice : 12766
1

Indice : 12787
5

Indice : 12793
X 

Indice : 12833
;.•> ih^u x " “(U I           Ù

Indice : 12834
1

Indice : 12836
3

Indice : 12868
0

Indice : 12869
3

Indice : 12917
• t» • 

Indice : 13136
<27

Indice : 13138
mm

Indice : 13432
Frébourg

Indice : 13436
0

Indice : 13444
3

Indice : 13675
mi 

Indice : 13698
..à

Indice : 13709
1

Indice : 13768
’ 

Indice : 13771
1

Indice : 14896
1

Indice : 14932
2

Indice : 26521

1. LOCALISATION GEOGRAPHIQUE DU PROJET

Indice : 26522

2. DEFINITION DES AIRES D’ETUDE

Indice : 26524

1. CONTEXTE TOPOGRAPHIQUE

Indice : 26525

2. CONTEXTE CLIMATIQUE 

Indice : 26526

2.1. AU NIVEAU DEPARTEMENTAL 

Indice : 26527

2.2. AU NIVEAU LOCAL 

Indice : 26528

2.3. GISEMENT SOLAIRE 

Indice : 26529

3

Indice : 49541
1.4.

Indice : 49542
 La

Indice : 49544
1.5.

Indice : 49545
 La

Indice : 49547
1.6.

Indice : 49548
 L'hydrologie

Indice : 49549
1.7.

Indice : 49550
 L'hydrogeologie

Indice : 49551
1.8.

Indice : 49552
 Les zones humides

Indice : 49553
1.9.

Indice : 49554
 Les risques naturels

Indice : 49555

II. LE MILIEU NATUREL

Indice : 49559
Etude des amphibiens

Indice : 49563
Etude des mammifères

Indice : 49565
Etude de la flore et des habitats

Indice : 49567
Conclusion de l'etude de l'etat initial du milieu naturel

Indice : 49568

III. LE MILIEU HUMAIN

Indice : 49570
Le contexte administratif

Indice : 49573
La

Indice : 49577
Les voies de communication

Indice : 49579
L'ambiance acoustique

Indice : 49581
Les activités economiques

Indice : 49583
Les risques industriels et technologiques

Indice : 49585
Les réglés d'urbanisme

Indice : 49587
Les contraintes et les servitudes techniques

Indice : 49588

IV. LE PAYSAGE ET LE PATRIMOINE

Indice : 49593

V. LA SYNTHESE 


Indice : 159591
I. FICHE SIGNALETIQUE

Indice : 159592

I. RESUME NON TECHNIQUE

Indice : 159593

II. PRESENTATION DU PROJET

Indice : 159594
II. 1   Identification du demandeur

Indice : 159595
II.2 Localisation des ouvrages

Indice : 159596

II. 2.1    Forage d ’Angeîviille-Bailleul

Indice : 159597

II.2. 2 Forage de Saint-Maclou la Brière

Indice : 159598

II.2. 3    Périmètres de protection

Indice : 159599
II.3 P

Indice : 159602

II. 3.1 Nature de l IOTA

Indice : 159603

II. 3.2    Consistance de l’IOTA

Indice : 159604

II. 3.3 Volume de l’IOTA

Indice : 159605
II.4 N

Indice : 159607

II. 4.1    Loi sur l ’eau

Indice : 159608

II. 4.2    Etude d'impact

Indice : 159609

II.4.3 Natura 2000

Indice : 159611

II.4.5 Etude de bassin d’alimentation de captages

Indice : 159612

III. ETUDE DES IMPACTS

Indice : 159613

III. 1 Introduction

Indice : 159615
 Analyse de l’etat initial

Indice : 159616

III.2.1 Cadre géographique

Indice : 159617

III.2.2 Topographie et eaux superfic


Indice : 235067

1. LE PROJET

Indice : 235068

2. SITUATION GEOGRAPHIQUE - ACCES

Indice : 235069
2.1.

Indice : 235071
2.2.

Indice : 235072
 Surfaces et occupation des lieux

Indice : 235073
2.3.

Indice : 235076
OPERATIONNELLE

Indice : 235077
3.1.

Indice : 235078
 Description de la méthode d’exploitation

Indice : 235079
3.2.

Indice : 235080
 Principales données chiffrées

Indice : 235081
3.3.

Indice : 235082
 Ressources naturelles utilisées

Indice : 235083
3.4.

Indice : 235085
3.5.

Indice : 235086
 Description de la phase opérationnelle du projet

Indice : 235087

3.5.1. Travaux d'extraction

Indice : 235088

3.5.2. Stockage et évacuation des matériaux

Indice : 235089

3.5.3. Concassage et criblage.....................■.

Indice : 235090

3.5.4. Destination des matériaux

Indice : 235091

3.5.5. Apports de matériaux extérieurs

Indice : 235092

3.5.6. Remise en état

Indice : 235093
3.6.

Indice : 235094
 Demande et utilisation de l’energie

Indice : 235095

4. RESIDUS ET


Indice : 258611
SOMMAIRE

Indice : 258612
1 CONTEXTE DE L’ETUDE 

Indice : 258615
4 ANALYSE DE L’ETAT INITIAL DE LA ZONE ET DES MILIEUX

Indice : 258616
SUSCEPTIBLES D’ETRE AFFECTES PAR LE PROJET

Indice : 258617

4.1 LOCALISATION ET CARACTERISATION DU SITE

Indice : 258618
4.1.1

Indice : 258619
 C

Indice : 258620
ontexte geographique general

Indice : 258621
 

Indice : 258622
4.1.2

Indice : 258623
 R

Indice : 258624
eferences cadastrales

Indice : 258625

4.2 INVENTAIRE DES PLANS, SCHEMAS, PROGRAMMES, ET AUTRES

Indice : 258626
DOCUMENTS DE PLANIFICATION 

Indice : 258627
4.2.1

Indice : 258628
 A

Indice : 258630
 

Indice : 258631

4.2.1.1 Autres documents de planification

Indice : 258632

4.3 DEFINITION DES AIRES D’ETUDE 

Indice : 258633

4.4 ENVIRONNEMENT HUMAIN ET INDUSTRIEL DU PROJET

Indice : 258634
4.4.1

Indice : 258635
 V

Indice : 258636
oisinage immediat

Indice : 258637
4.4.2

Indice : 258638
 P

Indice : 258640
 

Indice : 258641
4.4.3

Indice : 258642
 C

Indice

Tableau 14 : Qualité des eaux à proximité du site 

Indice : 259086

Tableau 15 : Mesures à mettre en œuvre par les industriels 

Indice : 259087

Tableau 16 : Objectifs d’état écologique et chimique 

Indice : 259088

Tableau 17 : Arrêtés de reconnaissance de catastrophe naturelle relatifs à des inondations

Indice : 259089

Tableau 18 : Données de comptage sur les voies de circulation voisines

Indice : 259090

Tableau 19 : ZNIEFF figurant dans un rayon de 5 km des installations projetées 

Indice : 259091

Tableau 20 : Site Natura 2000 figurant dans un rayon de 5 km autours des installations projetées53

Indice : 259092

Tableau 21 : Synthèse de la sensibilité du milieu 

Indice : 259093
Tableau 5.1 : Caractérisation des eaux sanitaires - valeurs réglementaire (Arrêté du 2 février 1998) 

Indice : 259094
Tableau 5-2 : Caractéristiques des cheminées du site d’EUROLINKS SPIR-DEFENSE. présentant un

Indice : 259095
traitement des rejets atmosphériques 

Indice : 259096
Tableau 5-3 : No

12.2 Héliodons et risques d’éblouissements 

Indice : 280597
VARIANTES

Indice : 280598

12.3 Etudes sur l’enveloppe du bâtiment 

Indice : 280599

12.4 Etude de l’échauffement du verre 

Indice : 280600

12.5 Etude du rayonnement solaire intérieur 

Indice : 280601

12.6 Etudes sur les systèmes 

Indice : 280602

12.7 Etudes sur les hypothèses 

Indice : 280603
INTRODUCTION

Indice : 280622
2

Indice : 280676
2

Indice : 280864
Et S0 

Indice : 281004
2

Indice : 281225
• 

Indice : 281228
• 

Indice : 281398
• 

Indice : 281433
• 

Indice : 281977
Cl 

Indice : 282351
2

Indice : 282590
2

Indice : 282793
2

Indice : 282794
2

Indice : 283005
2

Indice : 283207
2

Indice : 283278
VARIANTES

Indice : 283284
2

Indice : 283302
- 

Indice : 283365
2

Indice : 283426
2

Indice : 283487
2

Indice : 283496

5 typologies sont étudiées :

Indice : 283537
+ 50% perforation

Indice : 283557
• 

Indice : 283559
2

Indice : 283560
2

Indice : 283563
2

Indice : 283566
2

Indice : 283567
2

Indic

Indice : 294770

5.6.3 Synthèse des impacts 

Indice : 294771

5.6.4 Mesures d’évitement et de réduction 

Indice : 294772

5.6.5 Impacts résiduels

Indice : 294773

5.6.6 Mesures de compensation et d’accompagnement 

Indice : 294774
5.7

Indice : 294775
 Impacts et mesures sur les emissions sonores

Indice : 294776
 

Indice : 294777

5.7.1 Mesures d’évitement en phase conception 

Indice : 294778

5.7.2 Impacts bruts 

Indice : 294779

5.7.3 Synthèse des impacts 

Indice : 294780

5.7.4 Mesures d’évitement et de réduction 

Indice : 294781

5.7.5 Impacts résiduels

Indice : 294782

5.7.6 Mesures de compensation et d’accompagnement 

Indice : 294783
5.8

Indice : 294784
 Impacts et mesures sur la circulation et le trafic

Indice : 294785
 

Indice : 294786

5.8.1 Mesures d’évitement en phase conception 

Indice : 294787

5.8.2 Impacts bruts 

Indice : 294788

5.8.3 Synthèse des impacts 

Indice : 294789

5.8.4 Mesures d’évitement et de réduction 

Indice : 294790

5.8.5 Impacts résidu

Indice : 295160

Figure 75 : Cartographie du bruit particulier pour la simulation de la phase n°1 

Indice : 295161

Figure 76 : Caractérisation des sources sonores pour la simulation de la phase n°2

Indice : 295162

Figure 77 : Cartographie du bruit particulier pour la simulation de la phase n°2 

Indice : 295163

Figure 78 : Caractérisation des sources sonores pour la simulation de la phase n°4

Indice : 295164

Figure 79 : Cartographie du bruit particulier pour la simulation de la phase n°4 

Indice : 295165

Figure 80 : Photographie prise depuis le pôle touristique de Saint-Nazaire-en-Royans mettant en avant la non-visibilité du projet depuis ce site

Indice : 295166

Figure 81 : Schéma explicatif de l’accès principal au site depuis la D532 

Indice : 295167

Figure 82 : Localisation de la cuve et du puits d’infiltration 

Indice : 295168

Figure 83 : Exemple de l’Abaque de Doury 

Indice : 295169

Figure 84 : Schéma conceptuel des enjeux et voies d’exposition 

Indice : 295170

F

In [176]:
c=train_active.label_RF.values

c[2107:26521]=np.zeros(26521-2107)
c[277263:278418]=np.zeros(278418-277263)
c[278867:280569]=np.zeros(280569-278867)
c[280603:294368]=np.zeros(294368-280603)

train_active['label']=c
train_active

/data/dataiku/data_dir_design/code-envs/python/THEO_/lib/python3.6/site-packages/ipykernel_launcher.py:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  


phrase  num_etude                                           phrase_2         0  ventre_0  ventre_1  ventre_2  ventre_3  ventre_4  ventre_5  ventre_6  ventre_7  ventre_8  ventre_9  ventre_10  ventre_11   33   34   35   36   37   38   39    f_mots   f_carac  html_carac  ind_sommaire  sommaire_longueur  sommaire_int  caractere_spec  label_k_3  label_RF  label
296183  <h6><a name="bookmark923"></a><span class="fon...     106905                          Risque rupture de barrage  0.004255  0.953618  0.562263  0.199909  0.652759  0.106185  0.391722  0.457804  0.335273  0.270279  0.344049   0.202554   0.247555  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.008523  0.010340    0.027999           1.0                0.0           0.0             0.0          1       0.0    0.0
296184  <p><a name="bookmark925"></a><span class="font...     106905                                         Définition  0.004255  0.419483  0.819485  0.423600  0.218639  0.215679  0.278888  0.479132  0.375938  0.520773  0.237621   0.112565   0.268572  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.003878    0.030195           1.0                0.0           0.0             0.0          1       0.0    0.0
296185  <span class="font6">Un barrage est un ouvrage,...     106905  Un barrage est un ouvrage, le plus souvent art...  0.004255  0.952355  0.560512  0.194462  0.650605  0.105932  0.388558  0.470029  0.326538  0.276844  0.327395   0.212637   0.244277  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.147727  0.152951    0.101839           1.0                1.0           0.0             0.0          1       0.0    0.0
296186  <span class="font6" style="font-weight:bold;">...     106905  les ruptures de barrage sont des accidents rar...  0.004255  0.604507  0.938026  0.572990  0.565242  0.136513  0.395126  0.447812  0.340989  0.413722  0.309174   0.123329   0.263178  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.028409  0.026282    0.028273           1.0                0.0           0.0             0.0          1       0.0    0.0
296187  <p><a name="bookmark927"></a><span class="font...     106905                        Manifestation de la rupture  0.004255  0.419483  0.819485  0.423600  0.218639  0.215679  0.278888  0.479132  0.375938  0.520773  0.237621   0.112565   0.268572  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.008523  0.011202    0.034861           1.0                0.0           0.0             0.0          1       0.0    0.0
...                                                   ...        ...                                                ...       ...       ...       ...       ...       ...       ...       ...       ...       ...       ...       ...        ...        ...  ...  ...  ...  ...  ...  ...  ...       ...       ...         ...           ...                ...           ...             ...        ...       ...    ...
596178  <td rowspan="2" style="vertical-align:middle;"...    1130980                                 \nNom scientifique  0.004255  0.164178  0.557958  0.005263  0.562748  0.209986  0.387602  0.471471  0.390108  0.377766  0.321405   0.216073   0.145992  0.0  0.0  0.0  0.0  0.0  1.0  0.0  0.002841  0.006894    0.025254           0.0                0.0           0.0             0.0          0       0.0    0.0
596179  <td rowspan="2" style="vertical-align:middle;"...    1130980                             \nStatut de protection  0.004255  0.164178  0.557958  0.005263  0.562748  0.209986  0.387602  0.471471  0.390108  0.377766  0.321405   0.216073   0.145992  0.0  0.0  0.0  0.0  0.0  1.0  0.0  0.005682  0.008617    0.026352           0.0                0.0           0.0             0.0          0       0.0    0.0
596180  <td rowspan="2" style="vertical-align:middle;"...    1130980                               \nStatut Natura 2000  0.034043  0.082548  0.234004  0.313908  0.608004  0.174968  0.339463  0.468541  0.367329  0.375597  0.311770   0.230750   0.151273  0.0  0.0  0.0  0.0  0.0  1.0  0.0  0.005682  0.007755    0.025803           0.0                0.0          

In [231]:
vide=[i for i in np.unique(train_active.num_etude) if train_active[train_active.num_etude==i].label_RF.sum()==0]
vide

[112862, 1078725, 1098190]

##### Absence de sommaire pour les études 112862 et 1078725

In [232]:
#for i in vide:
i=vide[-1]
print("########################################## \n",i,"\n")
for k in train_active[train_active.num_etude==i].phrase_2:
    print(list(train_active[train_active.num_etude==i].phrase_2).index(k))
    print(k,"\n")

########################################## 
 1098190 

0
@ 

1
SERL 

2
amenaGemenr 

3

ZAC BRON TERRAILLON
 

4
Étude d’impact 

5
Version finale - 20/07/2017 

6
IDENTIFICATION ET RÉVISION DU DOCUMENT 

7
IDENTIFICATION DU DOCUMENT 

8

Projet 

9

ZAC Bron Terraillon 

10

Maître d’Ouvrage 

11

SERL 

12

Document 

13

Étude d’impact 

14

Version 

15

Version finale 

16

Date 

17

20/07/2017 

18
SOMMAIRE 

19
1. 

20
 P 

21
réambule 

22
2. 

23
 R 

24
ésumé non technique 

25

2.1. Notion de programme  

26

2.2. Justification du projet  

27

2.2.1. La commune de Bron  

28

2.2.2. Le quartier Terraillon  

29

2.2.3. L’opération de renouvellement urbain Terraillon  

30

2.3. Présentation du projet  

31

2.3.1. Les trois projets des études de définition initiales 

32

2.3.2. Le projet du dossier de création de ZAC approuvé le 20 septembre 2010 par la Métropole de Lyon  

33

2.3.3. L’évolution du projet  

34

2.3.4. Présentation du projet  

35

2.4. Etat initial de 

228
atura 

229
 2000 

230
12. 

231
 C 

232
ompatibilité avec les documents de planification 

233
13. 

234
 D 

235
ispositif de suivi et coût des mesures en faveur de 

236
l 

108
’ 

111
environnement 

239

13.1. Dispositif de suivi en phase chantier 

240

13.2. Dispositif de suivi en phase exploitation  

241

13.3. Coûts des mesures 

242

13.4. Effets attendus des mesures  

243
| 

244
 14. A 

245
nalyse des effets cumulés avec d 

108
’ 

247
autres projets connus 

248
372 

249

14.1. Contexte réglementaire 

250

14.2. Projets concernés par les effets cumulés  

251

14.3. Analyse des effets cumulés de la ZAC Bron Terraillon 

252

14.3.1. Avec la ZAC les Terrasses à Bron 

253

14.3.2. Avec la ligne de tramway T6 Debourg / Mermoz / Hôpitaux Est 

254

14.3.3. Avec le projet de restructuration des galeries Lafayette 

255

14.3.4. Avec le projet de renouvellement urbain du quartier Parilly  

256
| 15. A 

257
nalyse des méthodes utilisées 

258

15.1 .  Méthodes d’a

395

Figure 109 : Site Natura 2000  

396

Figure 110 : Carte des essences 

397

Figure 111 : Localisation des arbres d’alignements, espaces végétalisés à mettre en valeur, EBC 

398
(Grand Lyon) 

399

Figure 112 : Localisation des inventaires réalisés par le CBNMC 

400

Figure 113 : Square urbain 

401

Figure 114 : Alignement de Cyprès  

402

Figure 115 : Alignement de Cerisiers  

403

Figure 116 : Localisation des arbres d’alignements, espaces végétalisés à mettre en valeur, EBC 

398
(Grand Lyon) 

405

Figure 117 : Friche industrielle  

406
Figure 118 :  

407
Potager privé entretenu 

101
  

409

Figure 119 : Jardin ornemental 

410
Figure 120 :  

411
Bâtiments 

101
  

413

Figure 121 : Bâtiment pouvant convenir aux Chiroptères  

414

Figure 122 : Carte des milieux naturels  

415

Figure 123 : Grands axes 

416

Figure 124 : Historique des interventions sur le quartier Terraillon  

417

Figure 125 : Le projet « Carré de Soie » 

418
Figure 126 : Projet de la ZAC les 

545
Lyonnais 

546

Tableau 26 : Mesures spécifique de la masse d’eau Miocène sous couverture Lyonnais et sud 

547
Dombes - FRDG240 

548

Tableau 27 : Mesures spécifique de la masse d’eau Couloirs de l’Est lyonnais (Meyzieu, Décines, 

549
Moins) et alluvions de l’Ozon 

550

Tableau 28 : Objectifs du PGRI Rhône Méditerranée 2016-2021 

551

Tableau 29 : Population par tranche d’âge en 2008 et en 2013 sur la commune de Bron  

552

Tableau 30 : Population par sexe et âge en 2013 sur la commune de Bron  

553

Tableau 31 : Population de 15 ans ou plus selon la catégorie socioprofessionnelle sur la commune de 

554
Bron  

555

Tableau 32 : Ménages selon leur composition sur la commune de Bron  

556

Tableau 33 : Population active de Bron de 15 à 64 ans par type d’activité en 2008 et 2013  

557

Tableau 34 : Taux de chômage sur la commune de Bron en 2008 et 2013  

558

Tableau 35 : Taux de chômage des 15-64 ans par sexe et par âge en 2013 sur la commune de 

559

Tableau 36 : Catégo

674
Le quartier Terraillon est un quartier prioritaire des politiques publiques, classé en quartier politique de la ville et fait partie intégrante du Réseau de Réussite Scolaire (RRS). 

675
Ce quartier est caractérisé par : 

627
• 

677
 des copropriétés privées fragilisées : immeubles construits dans les années 60, parc de copropriétés le plus important de l’agglomération, dégradation du bâti et des espaces extérieurs dégradés, .... 

627
• 

679
 Une grande fragilité sociale : 70.5 % de la population est sans diplôme ou avec un diplôme niveau inférieur au BAC. 49.5 % des personnes de 15 à 64 ans ont un emploi (dont 21.4 % d’emplois précaires) alors que ce taux à l’échelle de la Métropole de Lyon est de 63.2 %. Mais le quartier Terraillon présente quelques atouts à conforter, fruit d’une intervention publique : il est doté d’équipements publics de proximité, de structures socio-culturelles (centre social, associations.) et est animé par des commerces de proximité ainsi que par un m

...

627
• 

2430
 Osier Blanc : Salix Viminalis, 

627
• 

2432
 Saule Marsault : Salix Caprea, 

627
• 

2434
 Bouleau nain : Betula nana, 

627
• 

2436
 Saule arctique compact : Salix Purpurea Gracilis. 

2437
O Traitements des limites espaces publics / espaces privatifs 

2438
Le traitement qualitatif des limites permet de différencier les espaces en fonction des usages recherchés ainsi que les limites de propriétés. Une attention particulière devra être apportée à leur traitement. Une grande cohérence et une certaine unité dans le vocabulaire architectural et paysager devra être recherché à l’échelle du quartier. 

2439
Le traitement des limites devra assurer la lisibilité de l’espace entre domaine public et privé, ainsi que l’isolement visuel des habitations en rez-de-chaussée. 

627
• 

2441
 Sur les espaces ne nécessitant pas de « contrôle d’accès » on privilégiera les limites symboliques par des changements de matériaux pour marquer les seuils publics / privés. 

627
• 

2443
 Sur

2532
Les recommandations de gestion des matériaux du site de Ginger Burgeap sont les suivantes : 

840
•  

2534
Favoriser le réemploi sur site des terres excavées 

2535
Les matériaux non inertes identifiés au droit des mailles S4 et S10 sur l’horizon superficiel, ne présentant pas d’impact par des composés volatils, sont donc susceptibles de faire l’objet d’une réutilisation dans le cadre du projet et d’une balance volumique déblais / remblais, sous réserve par ailleurs d’une qualité géotechnique adaptée. 

2536
Outre les avantages liés à l’aspect financier, ce mode de gestion est aujourd’hui le mieux adapté à la politique du ministère du Développement Durable (textes de la législation 2007), à savoir de privilégier la conservation des terres sur un site plutôt que l’élimination hors site. 

840
•  

2538
Évacuation hors site 

2539
Sur la base des caractéristiques du projet d’aménagement communiquées, par extrapolation des données environnementales acquises lors du diagnostic initia

2658
 Les récepteurs potentiels sont les populations susceptibles d’être exposés aux composés volatils. Sur la base des usages potentiels du terrain indiqués, les cibles exposées sont donc les futurs usagers : adultes et enfants. 

1016
Remarque : 

2660
 Les futurs travailleurs du chantier de terrassement n’ont pas été retenus comme cibles potentielles étant donné que ces derniers seront équipés d’équipement pour la protection de la santé. 

2661
Suite à la réalisation du schéma conceptuel (usage futur), des recommandations ont été proposées en ce qui concerne la gestion des terres : 

805
»  

2663
Favoriser le réemploi sur site des terres excavées non polluées, 

805
»  

2665
Évacuation hors site des terres non inertes et traitement dans des filières adaptées, 

805
»  

2584
En ce qui concerne les terres laissées en place, au vu de la qualité des matériaux sur site, il est recommandé de recouvrir par une surface étanche (enrobé, béton) ou par 30 cm de terres saines les terres supe

842
n 

842
n 

842
n 

842
n 

842
n 

842
n 

842
n 

842
n 

842
n 

842
n 

842
n 

842
n 

842
n 

842
n 

842
n 

842
n 

842
n 

842
n 

842
n 

842
n 

842
n 

842
n 

842
n 

842
n 

842
n 

627
• 

2849
 Des terres et sols pollués à évacuer en raison notamment du passé industriel de certains secteurs, 

627
• 

2851
 Des déchets solides divers liés à la réalisation des travaux de voirie, du génie-civil d’une grande variété : coulis de ciments ou bétons, ferrailles, bois, plastiques divers, papiers et cartons, verre. 

627
• 

2853
 Des rejets ou émissions liquides : eaux pluviales de lessivage de terrassement ou de chantier, assainissement de chantier, hydrocarbures. 

627
• 

2855
 Des déchets d’équipements publics liés à la suppression du city stade existant à côté de l’église : enrobés, grillages, panneaux de basket, cages de football.. 

627
• 

2857
 Des déchets verts : 

842
n 

842
n 

842
n 

627
• 

2862
 Des déchets alimentaires liés à la vie sur le chantier, 

2863

KeyboardInterrupt: 

In [251]:
c=np.zeros(len(train_active[train_active.num_etude==i].phrase_2))
c[18:624]=np.ones(624-18)
idx=train_active[train_active.num_etude==i].index[0]
train_active.loc[18+idx:624+idx,'label']=1
train_active[train_active.num_etude==i][18:100]

/data/dataiku/data_dir_design/code-envs/python/THEO_/lib/python3.6/site-packages/pandas/core/indexing.py:966: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self.obj[item] = s


phrase  num_etude                                           phrase_2         0  ventre_0  ventre_1  ventre_2  ventre_3  ventre_4  ventre_5  ventre_6  ventre_7  ventre_8  ventre_9  ventre_10  ventre_11   33   34   35   36   37   38   39    f_mots   f_carac  html_carac  ind_sommaire  sommaire_longueur  sommaire_int  caractere_spec  label_k_3  label_RF  label
508120  <h2><a name="bookmark4"></a><span class="font3...    1098190                                           SOMMAIRE  0.004255  0.604968  0.938563  0.574648  0.565981  0.136280  0.395973  0.444785  0.342574  0.412347  0.314423   0.121675   0.263757  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.003016    0.029371           1.0                0.0           0.0             0.0          1       0.0    1.0
508121  <span class="font30" style="font-weight:bold;"...    1098190                                                 1.  0.059574  0.522878  0.614071  0.881635  0.610497  0.101495  0.346988  0.444881  0.318209  0.411553  0.299539   0.138006   0.268459  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.000431    0.012078           1.0                1.0           0.0             0.0          1       0.0    1.0
508122  <span class="font30" style="font-weight:bold;f...    1098190                                                  P  0.004255  0.612047  0.957438  0.580750  0.596701  0.142287  0.407512  0.404134  0.308546  0.587354  0.090699   0.706144   0.144784  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.002841  0.000431    0.018666           1.0                1.0           0.0             0.0          1       0.0    1.0
508123  <span class="font29" style="font-weight:bold;f...    1098190                                           réambule  0.004255  0.612047  0.957438  0.580750  0.596701  0.142287  0.407512  0.404134  0.308546  0.587354  0.090699   0.706144   0.144784  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.003016    0.020313           1.0                0.0           0.0             0.0          1       0.0    1.0
508124  <span class="font30" style="font-weight:bold;"...    1098190                                                 2.  0.059574  0.522878  0.614071  0.881635  0.610497  0.101495  0.346988  0.444881  0.318209  0.411553  0.299539   0.138006   0.268459  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.000431    0.012078           0.0                0.0           0.0             0.0          1       0.0    1.0
508125  <span class="font30" style="font-weight:bold;f...    1098190                                                  R  0.004255  0.612047  0.957438  0.580750  0.596701  0.142287  0.407512  0.404134  0.308546  0.587354  0.090699   0.706144   0.144784  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.002841  0.000431    0.018666           0.0                0.0           0.0             0.0          1       0.0    1.0
508126  <span class="font29" style="font-weight:bold;f...    1098190                                ésumé non technique  0.004255  0.612047  0.957438  0.580750  0.596701  0.142287  0.407512  0.404134  0.308546  0.587354  0.090699   0.706144   0.144784  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.005682  0.007755    0.023332           0.0                0.0           0.0             0.0          1       0.0    1.0
508127  <li>\n<p><a href="#bookmark8"><span class="fon...    1098190                        \n2.1. Notion de programme   0.051064  0.400452  0.377514  0.834389  0.045256  0.607546  0.895715  0.468707  0.292211  0.451320  0.305309   0.168661   0.253249  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.011364  0.010771    0.029646           0.0                0.0           0.0             0.0          1       0.0    1.0
508128  <li>\n<p><a href="#bookmark9"><span class="fon...    1098190                    \n2.2. Justification du projet   0.051064  0.400452  0.377514  0.834389  0.045256  0.607546  0.895715  0.468707  0.292211  0.451320  0.305309   0.168661   0.253249  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.011364  0.012495    0.030744           0.0                0.0          

In [183]:
presque_vide=[i for i in np.unique(train_active.num_etude) if (train_active[train_active.num_etude==i].label_RF.sum()>0) and (train_active[train_active.num_etude==i].label_RF.sum()<50)]
presque_vide

[109735, 1094735]

In [186]:
i=presque_vide[-1]
print("########################################## \n",i,"\n")
for k in train_active[train_active.num_etude==i].phrase_2:
    print(list(train_active[train_active.num_etude==i].phrase_2).index(k))
    print(k,"\n")

########################################## 
 1094735 

0
MergedFile 

1
GUYOT Environnement 

2
__ Transit, regroupement, tri et traitement de déchets non dangereux et dangereux 

3
DOSSIER DE DEMANDE 

4
D'AUTORISATION 

5
ENVIRONNEMENTALE 

6
FASCICULE B - ETUDE 

7
D'IMPACT 

8
Rapport n°R17075_Ba 

9
Version de 14 juin 2019 

10
Risques Industriels | Environnement | Sécurité / Santé 

11
Carré Rosengart, 16 quai Armez, 22000 SAINT-BRIEUC Tél. : 02 96 65 79 31 | Courriel :  

12
contact@neodyme.bzh 

13
  

14
www.neodyme.bzh 

15
NANTES / SAINT NAZAIRE LORIENT RENNES BREST 

16
Fiche signalétique 

17
Client 

18

Raison sociale : 

19

GUYOT Environnement 

20

Adresse du siège social : 

21

15, rue Jean-Charles Chevillotte - 29200 BREST 

22

Représentant : 

23

Bertrand Le Floch | Représentant permanent 

24

Site 

18

Raison sociale : 

19

GUYOT Environnement 

27

Adresse du site : 

28

Zone Industrielle de Kérolzec - 29600 Saint-Martin-des-Champs 

29

Téléphone : 

30



184

6.7. Émissions lumineuses  

185

6.8. Patrimoine culturel  

186

6.9. Urbanisme  

187

6.9.1. Plan Local d’Urbanisme (PLU) de Saint-Martin-des-Champs 

188

6.9.2. Projet de Plan Local d’Urbanisme Intercommunal de Morlaix Communauté  

189

6.9.3. Schéma de Cohérence Territoriale (SCoT) de Morlaix Communauté  

190

6.10. Environnement sonore  

191

6.10.1. Sources de bruit dans l’environnement  

192

6.10.2. Niveaux sonores mesurés dans l’environnement 

193

6.11. Vibrations dans l’environnement  

194

7. Etat initial de la qualité de l’air  

195

7.1. Présentation de la règlementation applicable  

196

7.2. Qualité de l’air à l’échelle régionale  

197
7.2.1. Dioxyde d’azote (NO 

198
2 

199
)  

200

7.2.2. Particules Fines PM 10  

201

7.2.3. Particules Fines PM 2.5  

202

7.2.4. Ozone  

203
7.2.5. Dioxyde de Soufre (SO 

198
2 

199
)  

206

7.2.6. HAP Benzo(a)pyralène 

207

7.2.7. Benzène (représentatif des COVNM)  

208

7.2.8. Monoxyde de Carbone  

209

7.2

311

6.6.1. Nuisances liées aux émissions lumineuses  

312

6.6.2. Nuisances liées à la sécurité publique : effets temporaires et permanents et mesures  

313

6.6.3. Nuisances liées à la salubrité : effets temporaires et permanents et mesures  

314

6.7. Elimination / Valorisation des déchets  

315

6.7.1. Effets temporaires du projet en matière de déchets  

316

6.7.2. Incidence de l’exploitation en matière de déchets  

317

6.7.3. Mesures visant à éviter / réduire / compenser les effets liés à la production de déchets et à leur élimination / valorisation  

318

7. Risques pour la santé humaine, le patrimoine culturel et l'environnement  

319

7.1. Risque pour la santé humaine  

320

7.2. Risque pour le patrimoine culturel  

321

7.2.1. Rappel de la situation du site par rapport au patrimoine culturel  

322

7.2.2. Risques liés au projet sur le patrimoine culturel  

323

7.2.3. Mesures visant à éviter / réduire / compenser le risque sur le patrimoine culturel  

324

7.3. 

423
Tableau 100 : Résultats de l’autosurveillance des rejets d’eau pluviales  

424
Tableau 101 : Synthèse des analyses de la qualité des eaux de la Pennélé (campagne ponctuelle 2015)  

425
Tableau 102 : Analyse de la compatibilité des modalités de gestion des eaux avec les orientations/dispositions du SDAGE Loire-Bretagne 2016.2021  

426
Tableau 103 : Analyse de la compatibilité des modalités de gestion des eaux avec le programme de mesure spécifique du sous-bassin de la Vilaine et des côtiers bretons »  

427
Tableau 104 : Analyse de la compatibilité des modalités de gestion des eaux avec les dispositions et articles de règlement du SAGE « Léon -Trégor »  

428
Tableau 105 : Principales caractéristiques du point de rejet canalisé (broyeur) 

429
Tableau 106 : Coordonnées Lambert II étendu du point de rejet canalisé du flux d’air du broyeur 

430
Tableau 107 : Valeurs limites au niveau du rejet canalisé (article 3.2.3. de l’AP du 27/11/2017)  

431
Tableau 108 : Détail de la fréquen

521
Figure 121 : Localisations des ICPE à l’échelle du secteur d’étude 

522
Figure 122 : Cartographie des canalisations de transport de matières dangereuses (GéoRisques)  

523
Figure 123 : localisation du site d’étude 

524
Figure 124 : Détail de l’emprise cadastrale du site d’étude  

525
Figure 125 : Schéma des axes structurants et du développement économique du Scot de Morlaix Communauté 

526
Figure 126 : Extrait du Registre Parcellaire Graphique (RPG) de 2016  

527
Figure 127 : Extrait de la carte forestière (v2) sur le secteur d’étude  

528
Figure 128 : Localisation des ouvrages de suivi interne des eaux souterraines (piézomètres)  

529
Figure 129 : Illustration du bassin de gestion des eaux pluviales Nord  

530
Figure 130 : Illustration du bassin de gestion des eaux pluviales Nord  

531
Figure 131 : Illustration du caisson de filtration et de la cheminée du rejet canalisé de l’air de la ligne DND  

532
Figure 132 : Localisation du point de rejet canalisé du flux d’air de

...

8036
.) 

8037

- la présence avérée (Grenouilles vertes) et potentielle (Triton palmé, Salamandre tacheté, Grenouille agile.) d’amphibiens protégés 

8038

- la présence potentielle de reptiles protégés (Couleuvre à collier, Orvet fragile, Lézard vivipare, Coronelle lisse, Vipère péliade .) 

3166
■ 

8040
 le bassin nord-ouest de récolte des eaux pluviales du site qui est un habitat de reproduction d’amphibien protégés (Grenouilles vertes, Crapaud commun, Triton palmé.) (fig.2) 

3166
■ 

8042
 les strates boisées (haies au centre du site et haies longeant la route le long du site - (fig.7 & 9).) sont des habitats terrestres potentiels des amphibiens se reproduisant sur le site (dans la prairie humide sud-ouest, dans la rivière Pennélé, dans le bassin nord-ouest du site) et à l’extérieur du site (dans les mares de l’aire de stockage et de broyage de déchets verts et dans le bassin en eau de l’ancienne carrière de Kerolzec). Elles représentent également des milieux de reproduction d’o

8146
Dates de validation régionale et nationale 

8147
Date de premier avis CSRPN : 29/10/1999 

8148
Date actuelle d'avis CSRPN : 29/10/1999 

8149
Date de première diffusion INPN : 01/01/1900 

8150
Date de dernière diffusion INPN : 02/06/2015 

8151

1. DESCRIPTION  

8152

2. CRITERES D'INTERET DE LA ZONE  

8153

3. CRITERES DE DELIMITATION DE LA ZONE  

8154

4. FACTEUR INFLUENCANT L'EVOLUTION DE LA ZONE  

8155

5. BILAN DES CONNAISSANCES - EFFORTS DES PROSPECTIONS  

8156

6. HABITATS  

8157

7. ESPECES  

8158

8. LIENS ESPECES ET HABITATS  

8159

9. SOURCES  

8160
1. DESCRIPTION 

8161


1.1 Localisation administrative 

8162

- Département : Finistère 

8163

- Commune : Taulé (INSEE : 29279) 

8164

- Commune : Guiclan (INSEE : 29068) 

8165

1.2 Superficie 

8166
21,04 hectares 

8167

1.3 Altitude 

8168
Minimale (mètre): 5 

8169
Maximale (mètre): 50 

8170

1.4 Liaisons écologiques avec d'autres ZNIEFF 

8171
Non renseigné 

8172

1.5 Commentaire général 

8173
La Pe

8389

2009 

8390

Phanérogames 

8391

87471 

8392

Callitriche hamulata Kütz. ex W.D.J.Koch, 1837 

8393

Callitriche à crochets, Callitriche en hameçon 

8378

Reproduction certaine ou probable 

8379
Informateur : 

8380
HAURY Jacques 

8397

Fort 

8398

87476 

8399

Callitriche obtusangula Le Gall, 1852 

8400

Callitriche à angles obtus 

8378

Reproduction certaine ou probable 

8379
Informateur : 

8380
HAURY Jacques 

8381

Moyen 

8405

87480 

8406

Callitriche platycarpa Kütz., 1842 

8407

Callitriche à fruits plats, Callitriche à fruits élargis 

8378

Reproduction certaine ou probable 

8379
Informateur : 

8380
HAURY Jacques 

8381

Moyen 

8412

109864 

8413

Oenanthe crocata L., 1753 

8414

Oenanthe safranée 

8378

Reproduction certaine ou probable 

8379
Informateur : 

8380
HAURY Jacques 

3061

Faible 

8419

117165 

8420
Ranunculus penicillatus (Dumort.) 

8421
Bab., 1874 

8422

Renoncule à pinceau, Renoncule pénicillée 

8378

Reproduction certaine ou pro

8683

82952 

8684

Anthriscus sylvestris (L.) Hoffm., 1814 

8685

Cerfeuil des bois, Persil des bois 

8378

Reproduction certaine ou probable 

8379
Informateur : 

8380
HAURY Jacques 

3061

Faible 

8690

83912 

8691
Arrhenatherum elatius (L.) P.Beauv. ex J.Presl 

8692
& C.Presl, 1819 

8693

Fromental élevé, Ray-grass français 

8378

Reproduction certaine ou probable 

8379
Informateur : 

8380
HAURY Jacques 

3061

Faible 

8181
ZONES NATURELLES D'INTÉRÊT ÉCOLOGIQUE, FAUNISTIQUE ET FLORISTIQUE 

8365

Groupe 

8366

Code Espèce (CD_NOM) 

8367

Nom scientifique de l'espèce 

8368

Nomm vernaculaire de l'espèce 

8369

Statut(s) biologique(s) 

8370

Sources 

8371

Degré d'abondance 

8372

Effectif inférieur estimé 

8373

Effectif supérieur estimé 

8374

Année/ Période d'observation 

8709

87915 

8710
Cardamine flexuosa 

8711
With., 1796 

8712

Cardamine flexueuse, Cardamine des bois 

8378

Reproduction certaine ou probable 

8379
Informateur : 

8380
HAURY Jacques 



KeyboardInterrupt: 

In [253]:
idx=train_active[train_active.num_etude==109735].index[0]
train_active.loc[36+idx:257+idx,'label']=1
train_active[train_active.num_etude==109735][36:100]

/data/dataiku/data_dir_design/code-envs/python/THEO_/lib/python3.6/site-packages/pandas/core/indexing.py:966: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self.obj[item] = s


phrase  num_etude                                           phrase_2         0  ventre_0  ventre_1  ventre_2  ventre_3  ventre_4  ventre_5  ventre_6  ventre_7  ventre_8  ventre_9  ventre_10  ventre_11   33   34   35   36   37   38   39    f_mots   f_carac  html_carac  ind_sommaire  sommaire_longueur  sommaire_int  caractere_spec  label_k_3  label_RF  label
489621  <p><span class="font7" style="font-weight:bold...     109735                                 Table des matières  0.004255  0.419483  0.819485  0.423600  0.218639  0.215679  0.278888  0.479132  0.375938  0.520773  0.237621   0.112565   0.268572  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.005682  0.007324    0.018117           0.0                0.0           0.0             0.0          1       0.0    1.0
489622  <p><a href="#bookmark9"><span class="font7" st...     109735                           Partie 1 :  Présentation  0.046809  0.377171  0.409984  0.801450  0.139722  0.482994  0.765168  0.680947  0.069900  0.604768  0.263037   0.079473   0.283968  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.008523  0.009910    0.026626           0.0                0.0           0.0             0.0          1       0.0    1.0
489623  <li>\n<p><a href="#bookmark10"><span class="fo...     109735           \n1.1. Présentation du porteur de projet  0.046809  0.400452  0.377514  0.834389  0.045256  0.607546  0.895715  0.468707  0.292211  0.451320  0.305309   0.168661   0.253249  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.014205  0.016372    0.033489           0.0                0.0           0.0             0.0          1       0.0    1.0
489624  <li>\n<p><a href="#bookmark11"><span class="fo...     109735                \n1.1.1 Le groupe WSB Neue Energien  0.046809  0.748300  0.000000  0.455861  0.130619  0.576965  0.889147  0.490925  0.277760  0.314441  0.323529   0.257970   0.234348  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.014205  0.014218    0.024979           0.0                0.0           0.0             0.0          1       0.0    1.0
489625  <li>\n<p><a href="#bookmark12"><span class="fo...     109735  \n1.1.2 VSB énergies nouvelles, un rayonnement...  0.046809  0.748300  0.000000  0.455861  0.130619  0.576965  0.889147  0.490925  0.277760  0.314441  0.323529   0.257970   0.234348  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.025568  0.030590    0.035410           0.0                0.0           0.0             0.0          1       0.0    1.0
489626  <li>\n<p><a href="#bookmark13"><span class="fo...     109735             \n1.2. Présentation des acteurs locaux  0.046809  0.400452  0.377514  0.834389  0.045256  0.607546  0.895715  0.468707  0.292211  0.451320  0.305309   0.168661   0.253249  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.011364  0.015511    0.032940           0.0                0.0           0.0             0.0          1       0.0    1.0
489627  <li>\n<p><a href="#bookmark14"><span class="fo...     109735        \n1.3. Localisation et présentation du site  0.046809  0.400452  0.377514  0.834389  0.045256  0.607546  0.895715  0.468707  0.292211  0.451320  0.305309   0.168661   0.253249  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.014205  0.017665    0.034312           0.0                0.0           0.0             0.0          1       0.0    1.0
489628  <li>\n<p><a href="#bookmark15"><span class="fo...     109735            \n1.4. Cadre politique et réglementaire  0.046809  0.400452  0.377514  0.834389  0.045256  0.607546  0.895715  0.468707  0.292211  0.451320  0.305309   0.168661   0.253249  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.011364  0.015941    0.033214           0.0                0.0           0.0             0.0          1       0.0    1.0
489629  <li>\n<p><a href="#bookmark16"><span class="fo...     109735         \n1.4.1 Engagements européens et nationaux  0.046809  0.748300  0.000000  0.455861  0.130619  0.576965  0.889147  0.490925  0.277760  0.314441  0.323529   0.257970   0.234348  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.011364  0.017234    0.026901           0.0                0.0          

In [255]:
idx=train_active[train_active.num_etude==1094735].index[0]
train_active.loc[53+idx:551+idx,'label']=1
train_active.loc[53+idx:551+idx,:]

/data/dataiku/data_dir_design/code-envs/python/THEO_/lib/python3.6/site-packages/pandas/core/indexing.py:966: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  self.obj[item] = s


phrase  num_etude                                           phrase_2         0  ventre_0  ventre_1  ventre_2  ventre_3  ventre_4  ventre_5  ventre_6  ventre_7  ventre_8  ventre_9  ventre_10  ventre_11   33   34   35   36   37   38   39    f_mots   f_carac  html_carac  ind_sommaire  sommaire_longueur  sommaire_int  caractere_spec  label_k_3  label_RF  label
459893  <h3><a name="bookmark6"></a><span class="font1...    1094735                       Sommaire de l’Etude d’Impact  0.004255  0.953318  0.561580  0.199681  0.652364  0.106011  0.391184  0.459173  0.334266  0.271187  0.340136   0.205760   0.246896  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.008523  0.011633    0.027724           0.0                0.0           0.0             0.0          1       0.0    1.0
459894  <span class="font27" style="font-weight:bold;"...    1094735                                          Partie I   0.004255  0.604507  0.938026  0.572990  0.565242  0.136513  0.395126  0.447812  0.340989  0.413722  0.309174   0.123329   0.263178  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.005682  0.003447    0.013999           0.0                0.0           0.0             0.0          1       0.0    1.0
459895  <span class="font6">Contexte méthodologique et...    1094735          Contexte méthodologique et réglementaire   0.004255  0.952355  0.560512  0.194462  0.650605  0.105932  0.388558  0.470029  0.326538  0.276844  0.327395   0.212637   0.244277  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.011364  0.017234    0.015372           0.0                0.0           0.0             0.0          1       0.0    1.0
459896  <li>\n<p><a href="#bookmark9"><span class="fon...    1094735                        \n1. Contexte réglementaire  0.042553  0.748300  0.000000  0.455861  0.130619  0.576965  0.889147  0.490925  0.277760  0.314441  0.323529   0.257970   0.234348  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.005682  0.010771    0.022783           0.0                0.0           0.0             0.0          1       0.0    1.0
459897  <li>\n<p><a href="#bookmark10"><span class="fo...    1094735  \n1.1. Introduction de la notion d’évaluation ...  0.042553  0.748300  0.000000  0.455861  0.130619  0.576965  0.889147  0.490925  0.277760  0.314441  0.323529   0.257970   0.234348  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.019886  0.026282    0.032940           0.0                0.0           0.0             0.0          1       0.0    1.0
...                                                   ...        ...                                                ...       ...       ...       ...       ...       ...       ...       ...       ...       ...       ...       ...        ...        ...  ...  ...  ...  ...  ...  ...  ...       ...       ...         ...           ...                ...           ...             ...        ...       ...    ...
460387  <p><a href="#bookmark473"><span class="font25"...    1094735                                            Europe   0.004255  0.806648  0.356425  0.114277  0.179830  0.487431  0.806739  0.706095  0.078229  0.470059  0.290893   0.154105   0.259786  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.002841  0.002585    0.015646           0.0                0.0           0.0             0.0          1       0.0    1.0
460388  <li>\n<p><a href="#bookmark474"><span class="f...    1094735  \nFigure 146 : Conséquences des variations sur...  0.042553  0.748300  0.000000  0.455861  0.130619  0.576965  0.889147  0.490925  0.277760  0.314441  0.323529   0.257970   0.234348  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.028409  0.030590    0.035959           0.0                0.0           0.0             0.0          1       0.0    1.0
460389  <li>\n<p><a href="#bookmark475"><span class="f...    1094735  \nFigure 147 : Evolution des températures annu...  0.042553  0.748300  0.000000  0.455861  0.130619  0.576965  0.889147  0.490925  0.277760  0.314441  0.323529   0.257970   0.234348  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.051136  0.040931    0.042547           0.0                0.0          

In [256]:
base_active=pd.concat([base.iloc[:,:-2],train_active.iloc[:,:-2]])
y_active=list(base.loc[:,'label_rf'])+list(train_active.loc[:,'label'])

In [257]:
base_active['label']=y_active

In [259]:
for i in base_active.index:
    try:
        if type(float(base_active.loc[i,'phrase_2']))==float:
            print(base_active.loc[i,'phrase_2'])
            base_active.loc[i,'label']=0
    except:
        continue


06
2019
10
11
12
2
2
2
2
2 
90
70 
2
1
1
2
3
2
3
2
2
2 
3
4
1
1
1.

650

660

214

266

32

50

0

5

23

30

0

20

12

26

3

24

1

28

3

12

0

20

938

1141

7

7

7
2

37

26

929.5

1206
20
31
20
30
20
31

25

27

17

25

10

27

17

25

10

27

17

25

10

08

19

25

03

08

19

25

27

17

25

10

27

17

25

10

27
19

25

10

27

03

08

19

25

03

08

19

25

03

08

19

25

27

17

25

10

27

17

25

10

17

25

27

17

25

10

27

17

25

10

420012981

420012994

420030228

420030372

420030374

6210

6510

9170

89


10

11.12

11.53
2
1
1
5
5
2
2

39

4

156

36

1

36

30

1

30

0.0014328
2
2

100

100

100

23

96

89

81

97

93

04

04

11

04

18

18

04

04

17

10

100

00

00

38

100

4

100

100

03

06

100

00

00

100

100

100

4

09

00

20
2
2
2

0
117 
13471
197
3
2018
2
2
3
2
2

6
 1 
 2 
 3
 4 
 5
158
1
2
2.
4.
2

2007


2009


2015


2008


2010


2014


2016


100

344
330
330
392
366
356
320
.378
359
354
442
409
358
293

22

2
2
92
2
3
2
2
 6


4342

73

10080

10080

10080

74

12453

2822

12453

15275

12453

15275

75

2556

2556

2556

2556

77

500

1559

375

1559

375

1934

375

1934

78

640

640

640

4115

79

6489

6489

80

4090

46380

4090

4090

4090

81

428

428

82

19132

19132

19132

19132

84

23115

86

14157

17634

17634

31791

17634

31791

87

26423

26423

26423

26423

92

7277

7277

7277

7277

93

10695

18695

18695

95

16313

16313

16313

16313

101

10070

2418

10070

2418

12400

2418

104

15737

6560

15737

6560

22297

22297

129

255

255

125

712

376

712

376

376

1088

127

2834

2334

2834

92689

992

16452

16452

16452

16452

994

5978

5978

5978

5978

1070

9046

9046

9046

9046

154176

154176

1934

0

1

2

3

4

5

6

1
1.1
1.2
1.3
1.4
1.5
2.1
2.2
2
2.3
2.4
2.5
6
7
5
8
8
2.6
2.7
2.8
3
3
2.9
3.1
2
3.2 
3.3
3.4
3
4.1
21
2
3
3
3
3
3

0.07
3

0.07

0.94
3
3
1
4.2 
4.3 
2
2
2
3
4.4
2
4.5
4.6 
3
4.7 
222
220
3
222
3
220
3
2
4
3
1
3
3
3

167

11

40

101

13

48

61



0

0

0

0

0

0

0

0

12

0

12

283

315

243

190

190

150

120

221

199

155

227

200

156

156

1

156

9

36

32

0

53

1

53

53

112

100

21

21

1

21

31

31

1

31

1018

1362
2 
2 
3
3
3
3
3

2002

2003

2004

2005

2006

2007

2008

2009

2010

2011

2012

2013

2014

2015

2016

2017

4

5

1

20

10

0

5

25

23

22

10

19

36

15

23

17

27

16

47

59

90

98

101

69

13

100

69

92

95

68

82

17

26

2

14

18

21

25

3

23

25

13

25

20

19

19

128

60

190

7

5

3

15

9

6

9

10

12

10

9

14

0

1

4

0

0

0

0

3

4

4

8

5

20

2

7

11

0

2

1

7

4

4

5

15

12

13

18

13

3

18

10

7

0

21

10

7

10

9

17

5

2

7

0

11

6

9

0

2

2

6

5

6

7

8

12

7

28

4

0

6

6

11

9

5

0

6

5

4

2

8

155

63

36

134

2

3

11

11

21

12

29

18

13

28

7

8

24

32

33

33

11

17

12

8

145

117

111

72

52

0

0

0

0

0

0

0

145

117

111

72

52

0

0

0

0

200

151

219

222

178

217

314

337

237

213

289

199




37

207

41

253

91

445

46

248

27

178

21

182

26

200

22

177

593

483

478

4
4
0 
0 
0 
0
0
0
0
0
0
0
4
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
4
1
1
0 
0
0
0
0
0
0
0
0
0
1
1
2
2
2
3
3
3
3
3
4
0
0
0
0
1
2
3
4
1
2
3
4
0
0
0
0
0
1
31
32

1

1

1

1

1

1

1

1

1
1
2
3
4
1 
2
3
4
1 
2 
3    
4    
2025
1
2
1
2
3
4
5
6
891
33
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0 
0 
0 
0 
0 
34
1
1
2
3

7600

1000

310000

130000

3600

2000

7000

5000

17000

13500

16300

13000

227500

187000

8870

8000

22700

20500

88000

85000

18837

20000

20815

25000

13100

19000
3
3

200000

45000

-5

182000

-4

20000

55000

600

2000

-1

26000

-1

3000

1200

8000

11000

-10

125000
3
3
3
3
2
3
3
3
3
3
35
35
35
35
36
1
3
3
0 
0 
2
0 
0 
0 
0 
37
38
2
1
0
0
0
0
0
0
0
0
0
0
0
0 
0 
0 
0
0
0
0
0
0
0
0
0
39
3
3
40
3
3
0 
0 
0 
0 
0 
0 
0 
0 
0 
0 
0
0
0
0
0
0 
0 
0
0
0
0
0
3
0 
0 
41
3
0
0
0
3
0
0
0
0
0
0
0
0
0
0

187

179

179

180
0 
0 
0 
0 
0 
0 
0 
0
0
0
0 
0 
0 
0
0
0 


2015

2016

2017

2018

59

64

115

46

173

457

243

362

232

419

359

323

1615

0.74

17

17

19

21

20

94

70

51

40

52

46

259

43

29

25

32

49

178

0.59

48

34

29

49

58

218

0.58

21

29

29

41

24

144

0.53

31

28

24

26

18

127

0.47

16

19

16

12

22

17

85

24

8

9

9

18

68

0.41

13

7

12

9

7

48

0.38

15

10

10

11

7

53

0.36

9

7

8

6

9

39

0.35

8

8

9

10

10

9

45

15

8

19

13

13

68

10

30

15

13

52

24

120

16

10

6

5

23

12

60

6

6

12

1

0

5

25

11

0

17

50

0

78

5

2

3

5

2

17

6

2

1

3

1

13

0.1

4

5

0

14

17

8

40

0.1

8

7

0

3

0

18

0.09

0

2

1

1

9

13

0

2

2

3

5

12

0.07

0

0

0

4

36

8

40

0.06

3

2

1

0

0

6

5

6

1

0

0

12

0

1

3

5

0

9

0

0

2

1

2

1

5

0

2

1

2

1

6

0

6

0

0

0

6

2

0

3

1

1

1.4

7

0.04

1

1

0

1

0

3

0

0

2

1

0

3

1

0

0

2

0

3

0

1

3

0

0

4

0

1

0

1

1

3

0

1

0

40

15

56

0.03

1

0

0

2

2

1

5

0

...


20.00

62.30

86.00

80.00

90.00

47.00

4.04

3.76

4.23

12.03

69.30

63.00

69.30

10.00

0.69

0.63

0.69

2.02

7.00

8.00

9.00

6.50

0.05

0.05

0.06

0.16
2016
2
2
2
3
1
2
1
2.1
10 
2.2
12.2 
2
2
2
2
2
12.3 
2
13.2 
2.1
2
2.2 
12.2
2
2
2
2
2
2
2
12.3
2
2
13.2 
2.1
2.2
1 
12.3 
2
2
2
2
2
2 
2
13.2 
2
2

1963

2000

1949

1960

26


27

30

21


34


27


21


23


15

31
28
12

32


26

6

2.20

1.2

187.20

187.00

187.00

187.50

188.1

1.8

2.0

187.3

187.1

1.5
1.5
23

1.5

1.5

1.0

1.5
4
5 
4
5
6
-6
-5
-4
-4
-5
5
6

1

69.0095

2

69.0152

3

69.0207
3

2016

2003

1991

1902

1972

1964

1954
3
3
3

1

4
1
3
1
1
2
4
2
3
3

1

4
1
2
3
3
4
2
6
12
6
3
4
5
2
2
4
2
2
10 
3
3
3
3
3
3
10
3
3
-3
-5
-5
3

2014

2013

2012

2011

2010

2009

2008

2007

2006

2014

2013

2012

2011

2010

2009

2008

2007

2006

2014

2013

2012

2011

2010

2009

2008

2007

2006

2014

2013

2012

2011

2010

2009

2008

2007

2006

2014

2013

2012

2011

2010

2009

2008

2007

2006

890
1


4

4

11

1

7

1

1

8

109

2

2

15

18

1

3

3
2004. 
7

50

50

50

50

50

50

1

50

1

50

1

50

2

50

1

50

1

50

1

50

1

50

1

50

1

50

1

50

6

50

8

50
1

1

50

1

50

2

50

1

50

1

50

8

50

10

8

50

1

8

50

1

8

50

1

8

020

50

1

8

50

14

50

1

14

1

14

50

50
7

010

50

50

50

50

50

50

50

50

50

50

50

50

50

50

50

50

50

50

21.00

50

50

50

4.55

50

4.55

50

50

15

50

15

50

10

50

10

50

10

50

10

50

2

50

2

22.56

50

2

23.16

50

2

0.20

50

2

50

3

50

1

50

1

2353

50

1

50

50

1

50

7

50

6

50

5

50

9

50

9

0.10

50

9

50

12

50

50

1

1

1

1

1

1

1

1

1

1

1

1

1

75
1

6

3

6

5

8

1

1

1

1

1

1

1

1

1

1

1

2

1
1

1

1
0
1
1

7

2

3

1

10

9
1

5

12

6

7

5

0

2

20

1

1

1

1

4

3

10

0

1

20

2

1

1

1

5

295

1

1

5

3

6

75

6

8

105

14

20

1

1

2

15

10

1

1

8

20

1

1

1

10

1

14

10

20

1

3

1

5

9

10

1

1

2

115

1

1

6

8

2

2

20


-4 
3
-3
3
3
3
3
-3
-3
-3
3
-4
-4
-4
-4
3
-7
-3
-3
-3
3
-3
-3
-3
-3
-3
-6
3
-1
-8
-4
-4
-4
-5
3
-1
-8
-3
-3
-3
-8
3
-8
-3
3
3
3

0

10

20

30

40

50

60

70

80

90

100

110

120

130

140

150
2
3 
3 
3 
3 
2
3 
3 
3
3

20170000

1

1

4
3
1
2
2 
 23
 2000 
1
2
2014
2

6.8

7.6

10.4

13.2

17.1

21.1

24

23.5

20.2

15.9

10.6

7.5

14.8

50.5

41.9

41.7

47.7

40.1

31.4

14.9

27.6

68.3

84.4

63.8

56

586.3
2
149
32
1
1

16

14

10

6

17

6

14

12

9

7
2

8

6

4

3
2

90

70

50

30
5
2

3

6

10

25

5

7

10

15
2

20

25

28
2

24

27

28
4

1

2

1

2

5
2

1
3

10

50

6

9

10
2
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
1
3
3
3
3

1

2

3

4
2

930020449

930012453

930020190
 2000

0

0

0

0

0

0

0

0

0

0

0

0

0

0

0

0

0

0

0

0

0

0

0

0

0

0

0

0

0

0

0

0

0

0

0

0

0

0

0

0

0

0

0

0

0

0

0

0

0

0

0

0

0

0

0

0

0

0

0

0

0

0

0

0

0

0
3
3
3
3
3
5
2
5
2 
2

4

3

3

3

3
2
2
4

735
2
1.
2.
2
2
2
2
2
2 

0

5

10

15

20

25

30

35

40


454939

0

0

0

1

0

447035

0

0

0

1

0

456003

0

0

0

1

0

456837

0

5

0

446905

0

0

452924

0

2

0

159604

0

2

0

706050

0

2

0

447749

0

1

0

446169

0

0

93803

0

0

674682

0

0

447041

1

0

453162

0

3

0

447188

0

2

0

448156

1

1

94972

0

3

0

447590

0

1

0

448459

0

448497

0

0

0

1

0

630983

0

0

0

1

0

706221

0

2

0

95965

0

3

0

446962

0

3

0

446244

0

0

192361

0

0

0

452876

0

3

0

639111

0

3

0

452879

0

0

445633

0

2

0

446713

0

0

0

1

0

670724

0

3

0

706340

0

2

0

445757

0

0

0

1

0

629883

0

0

1

0

446764

0

3

0

670773

0

3

0

629904

0

0

0

0

445580

0

3

0

629950

0

0

0

1

0

104811

0

0

0

1

0

104929

0

0

447354

0

5

0

447593

0

1

0

656475

0

5

0

728225

0

2

0

445678

0

2

0

447307

0

1

0

446894

0

1

0

447627

0

3

0

447356

0

3

0

447581

0

4

0

446234

0

0

0

109584

0

0

0

1

0

635141

0

2

0

110758

0

2

0

111876

0

4

0




9

11

8

12

4

1

5

14

13
1

11

4
1

12

4
1

13

4
1
25
2
0

8

4

15
5

28

8

20
6

0


In [260]:
from sklearn.model_selection import train_test_split
X_train,X_test,y_train,y_test=train_test_split(base_active.iloc[:,3:],base_active.iloc[:,-1],test_size=0.25,shuffle=True)

In [261]:
n=100 # On essaie avec 100 estimateurs

from sklearn.ensemble import RandomForestClassifier
RFC = RandomForestClassifier(n_estimators=n,verbose=0,class_weight="balanced")
RFC.fit(X_train, y_train)

print("Score train :",round(RFC.score(X_train,y_train),3))
print("Score test :",round(RFC.score(X_test,y_test),3))

from sklearn.metrics import confusion_matrix
print("Matrice de confusion sur le train \n",confusion_matrix(y_train,RFC.predict(X_train)))
print("Matrice de confusion sur le test \n",confusion_matrix(y_test,RFC.predict(X_test)))

Score train : 1.0
Score test : 1.0
Matrice de confusion sur le train 
 [[441503      0]
 [     0   5634]]
Matrice de confusion sur le test 
 [[147179      0]
 [     0   1867]]


In [262]:
da=dataiku.Folder('lZ0B3sSL')
import pickle
dico_Bagging={}
dico_Bagging['train']=[X_train,y_train]
dico_Bagging['test']=[X_test,y_test]
dico_Bagging['base']=base_active.iloc[:,:3]
dico_Bagging['modele']=RFC
pickle.dump(dico_Bagging,open(da.get_path()+"/dico_RF_active.pickle",'wb'))

#### On check les nouveaux résultats

In [200]:
base_finale

phrase  num_etude                                           phrase_2         0  ventre_0  ventre_1  ventre_2  ventre_3  ventre_4  ventre_5  ventre_6  ventre_7  ventre_8  ventre_9  ventre_10  ventre_11   33   34   35   36   37   38   39    f_mots   f_carac  html_carac  ind_sommaire  sommaire_longueur  sommaire_int  caractere_spec  label_k_3  label_RF
0                          <title>EI Munchhouse_V3</title>    1003691                                   EI Munchhouse_V3  0.000000  0.903363  0.215909  0.521686  0.749125  0.022868  0.425675  0.689352  0.760611  0.452229  0.296891   0.228436   0.247048  0.0  1.0  0.0  0.0  0.0  0.0  0.0  0.002841  0.006463    0.005215           0.0                0.0           0.0             0.0          1       0.0
1        <h1><a name="bookmark0"></a><span class="font2...    1003691                                                 06  0.187234  0.523014  0.614289  0.882017  0.610726  0.101309  0.347138  0.444512  0.318033  0.411697  0.300860   0.137647   0.268558  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.000431    0.027724           0.0                0.0           0.0             0.0          1       0.0
2        <p><span class="font20" style="font-weight:bol...    1003691                                               2019  0.085106  0.337854  0.495530  0.732244  0.263894  0.180661  0.230749  0.476202  0.353159  0.518603  0.227985   0.127242   0.273854  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.001293    0.014548           0.0                0.0           0.0             0.0          1       0.0
3        <p><span class="font14">Agence Aquitaine</span...    1003691                                   Agence Aquitaine  0.004255  0.767331  0.441971  0.045072  0.304002  0.185098  0.272320  0.501349  0.361487  0.383894  0.255841   0.201873   0.249672  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.002841  0.006463    0.010705           0.0                0.0           0.0             0.0          1       0.0
4                <p><span class="font14">SAFEGE</span></p>    1003691                                             SAFEGE  0.004255  0.767331  0.441971  0.045072  0.304002  0.185098  0.272320  0.501349  0.361487  0.383894  0.255841   0.201873   0.249672  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.002154    0.007960           0.0                0.0           0.0             0.0          1       0.0
...                                                    ...        ...                                                ...       ...       ...       ...       ...       ...       ...       ...       ...       ...       ...       ...        ...        ...  ...  ...  ...  ...  ...  ...  ...       ...       ...         ...           ...                ...           ...             ...        ...       ...
2443029  <span class="font21">Disponible sur le site de...     238301  Disponible sur le site de Réseau de Transport ...  0.004255  0.952355  0.560512  0.194462  0.650605  0.105932  0.388558  0.470029  0.326538  0.276844  0.327395   0.212637   0.244277  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.031250  0.028867    0.023058           0.0                0.0           0.0             0.0          1       0.0
2443030  <a href="http://www.clefdeschamps.info/"><span...     238301                     http://www.clefdeschamps.info/  0.004255  0.980319  0.503047  0.241811  0.570262  0.317373  0.758813  0.622318  0.129463  0.341865  0.353711   0.167576   0.254206  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.012495    0.024979           0.0                0.0           0.0             0.0          1       0.0
2443031  <p><sup><a href="#footnote14">14</a></sup><a n...     238301                                                 14  0.000000  0.761311  0.029575  0.430819  0.347951  0.290608  0.719598  0.978864  0.815095  0.711131  0.240078   0.170334   0.262575  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.000000  0.000431    0.016744           0.0                0.0           0.0             0.0          1       0.0
2443032  <sp

In [263]:
pred_active=RFC.predict(base_finale.iloc[:,3:-1])

In [264]:
base_finale['label_active']=pred_active

In [220]:
for i in base_finale[base_finale.label_active==1].phrase_2:
    print(i)

Sommaire

1.Résumé non technique

1.1 Présentation synthétique du projet 

1.2 Synthèse de l’état initial 

1.3 Synthèse des impacts et des mesures associées 

2.Présentation du demandeur 

2.1 Présentation générale d’ENGIE

2.2 ENGIE Green : un leader des énergies renouvelables en France 

2.3 Le solaire avec ENGIE Green 

2.4 Contacts

3.Description du projet 

3.1 Localisation du projet

3.2 Nature et objet de l’opération 

3.3 Généralités - Principe de base du photovoltaïque

3.4 Présentation des installations projetées

3.5 Travaux en vue de l’implantation des panneaux photovoltaïques

3.6 Mise en place d’un « chantier propre » 

3.7 Appréciation sommaire des dépenses 

3.8 Synthèse des caractéristiques générales et technique du projet 

3.9 Réglementation applicable 

4.Démantèlement et remise en état du site 

4.1 Devenir du site en fin de vie des modules 

4.2 Recyclage et valorisation des éléments

4.3 Remise en état des terrains 

5.Justification du choix d’aménagement et sol


3.2.3.5. Les espèces invasives 

3.2.3.6. Bilan patrimonial et enjeux biologiques 

3.3. CARACTERISTIQUES PAYSAGERES DE LA ZONE D’ETUDE 
3.3.1.
 Les vallonnements irreguliers du plateau
 
3.3.2.
 Les lacs et leurs rives
 
3.3.3.
 La vallee de la Blanchisserie et les autres vallons
 

3.4. PATRIMOINE CULTUREL 
3.4.1.
 Monuments historiques
 
3.4.2.
 Sites archeologiques
 
3.4.3.
 Zone de Protection du Patrimoine Architectural Urbain et Paysager
 

3.5. MILIEU HUMAIN 
3.5.1.
 Population
 
3.5.2.
 Activites economiques
 

3.5.2.1. L’agriculture 

3.5.2.2. Les autres activités économiques 
3.5.3.
 Documents d’URBANISME
 : 
3.5.4.
 Voirie et dessertes
 

3.5.4.1. Structure et fonctionnalités du réseau viaire 

3.5.4.2. Trafics sur la RD 258
3.5.5.
 Reseaux
 
3.5.6.
 Environnement sonore
 

3.5.6.1. Définitions 

3.5.6.2. Contexte réglementaire 

3.5.6.3. Présentation du site et de la mesure acoustique 

3.5.6.4. Résultats de la mesure et définition des critères 

4. ETUDES PREALABLES A LA 

3.5 Continuités écologiques

3.6 Habitats naturels et flore

3.6.1 Espèces végétales recensées

3.6.2 Espèces végétales à statut

3.6.3 Espèces exotiques envahissantes

3.6.4 Habitats naturels

3.7 Zones humides

3.8 La faune

3.8.1 Avifaune

3.8.2 Chiroptères

3.8.3 Mammifères non volants

3.8.4 Reptiles

3.8.5 Amphibiens

3.8.6 Insectes

3.9 Synthèse des enjeux écologiques

4. L'environnement humain

4.1 Activités humaines

4.1.1 Démographie

4.1.2 Logements résidentiels

4.1.3 Activités économiques et emploi

4.1.4 Les activités présentes à proximité du projet du parc solaire

4.2 Les documents de planification et d’orientation

4.2.1 Le Schéma Régional Climat Air Energie (SRCAE) Bourgogne

4.2.2 Un Plan Climat Energie Territorial (PCET) en Bourgogne

4.2.3 Le PCET de la Nièvre

4.2.4 Schéma de Cohérence Territoriale (SCoT)

4.2.5 Le cadastre

4.2.6 Le Plan Local d'Urbanisme de Tracy-sur-Loire

4.2.7 Servitude d’utilité publique

4.2.8 Un projet d’intérêt collectif

4.3 Les risques 

3
3
3
3
2
2
2
2
2
3
3
3
3
3
3
3
3
3
3
3
3
3
Lanj
1
SC310 
SC310 
La 
 ?
1
£ 
lOngaeime
1
1
1
Tourisme
1
S^sserait
niaiserie
Coudreau/
Wfesbyter
Beauvenms
Vaugôuswt
^Haussait
Réhoraie.
7
<5^ 
6
0
1
1
à 
à 
à 
à 
Formusson
Longuenée
1
Directive
 : 
mare
mare
mare
(Sierro et Arlettaz, 
(Rodrigues étal,
(Dietz étal/.,
: 
(Maillard et Monfort,
(Maillard et Monfort,
Bas et Bas,
 1817)
 1817)
(Arthur et Lemaire, 
 1817)
(Swift et Racay,
 1774)
(Gebhard et Brogdanowicz,
(Meschede et          
 1800)
(Medar et lecoq,
 1774)
(Bas et al,
 1817)
 1774)
La 
La 
La 
La 
2
2
3
,k 
1
I 
1
0
1
1
ï '
 I
 ;,G;^ 
1
Sceurdres
MCmtiêuiL
-de-feiny
1
1
’k 
SaLirdros
5
1
8
1
 K 
2
2
2
Enjeux identifies du territoire
 : Echelle de couleur des niveaux de sensibilité
 : 
 : 
 
Avifaune :
 
Chiroptères :
 
Autre faune :
 
 C - V
ariantes et justification du projet
1 Contexte politique et énergétique du projet 

2 Raisons du choix de la zone d’implantation du projet 
2 - 1 Intégration au Schéma Régional Climat Air 

4.9.2 Mesures pour éviter, réduire, compenser 
4.10
 E
 

4.10.2 Mesures pour éviter, réduire, compenser 
4.11
 Z
ones agricoles et les espaces forestiers et maritimes

4.11.2 Mesures pour éviter, réduire, compenser 
4.12
 F
aune
, 
, 
habitats et espaces naturels

4.12.2 Mesures pour éviter, réduire, compenser 
4.13
 E
valuation des incidences sur 

4.13.1 Rappel des points-clés du site 

4.13.2 Le site Natura 2000 FR7200661

4.13.3 Le réseau Natura 2000 

4.13.4 Synthèse du descriptif de l’installation 
4.13.5

4.13.6 Conclusion sur l’atteinte ou non portée à l’intégrité du site Natura 2000 
4.14
 D
 

4.14.2 Mesures pour éviter, réduire, compenser 
4.15
 C
onsommation energetique

4.15.2 Mesures pour éviter, réduire, compenser 
4.16
 R
ayonnements ionisants
 
4.17
 C
hamps electromagnetiques

5 EVALUATION DES RISQUES SANITAIRES 
5.1
 P
 
5.2
 P
resentation generale de la methodologie
 

5.2.1 Objectifs 

5.2.2 Méthodologie 
5.3
 E
valuation des emissions de l
INSTALLATION
 

5.3.1 I

...

1.3.7 Impacts sur la santé

1.4 Mesures envisagées pour prévenir, protéger et compenser les impacts sur l’installation 

1.4.1 Mesures de protection du milieu naturel et des paysages

1.4.2 Mesures pour limiter l’impact sur les eaux et les sols 

1.4.3 Mesures liées aux rejets atmosphériques 

1.4.4 Mesures pour limiter les émissions de bruit et les vibrations 

1.4.5 Réduction des consommations énergétiques 

1.5 Gestion des effluents d’élevage 
 R
esume non technique de l
’
ETUDE de dangers
 

2.1 Présentation générale 

2.2 Description et caractérisation de l’environnement 

2.3 Installations et procédés mis en œuvre sur le site 

2.4 Identification des phénomènes dangereux 

2.4.1 Potentiels de dangers externes 

2.4.2 Potentiels de dangers internes

2.4.3 Etude de l’accidentologie 

2.5 Analyse des risques 

2.6 Mesures de prévention 

2.7 Moyens de protection et d’intervention 

2.7.1 Moyens de secours internes 

2.7.2 Moyens de secours externes

2.7.3 Consignes de sécurité

SECT


4.2.9.2. Synthèse

4.2.10. Evolution du milieu humain

4.2.11. Synthèse des enjeux associés au milieu humain
 Milieu naturel

4.3.1. Contexte écologique du territoire étudié

4.3.1.1. Zones réglementées au titre de Natura 2000

4.3.1.2. Arrêté Préfectoral de Protection de Biotope

4.3.1.3. ZNIEFF (Zone Naturelle d’intérêt Ecologique, Faunistique et Floristique)

4.3.1.4. Zones humides

4.3.1.5. Synthèse des enjeux écologiques liés aux espaces naturels remarquables

4.3.1.6. Continuités écologiques du territoire étudié

4.3.2. Diagnostic fonctionnel et évaluation écologique de la zone d’étude

4.3.2.1. Présentation de l’occupation des sols du territoire d’étude

4.3.2.2. Espèces floristiques recensées sur la zone d’étude

4.3.2.3. Habitats naturels et semi-naturels identifiés sur la zone d’étude

4.3.2.4. Espèces faunistiques recensées sur la zone d’étude élargie

4.3.2.5. Analyse des continuités écologiques au sein de la zone d’étude
floristiques et faunistiques
d’étude élargie

4.3.2

Figure 12 : Aléa retrait gonflement des argiles 

Figure 13 : Localisation du site sur le zonage sismique français 

Figure 14 : Coupe hydrogéologique interprétative 

Figure 15 : Carte piézométrique - Nappe du Coniacien basses eaux 2017 

Figure 16 : Bassin versant hydrogéologique intercepté par la carrière 

Figure 17 : Enjeux vis-à-vis des usages de l’eau 

Figure 18 : Évolution des volumes pompés dans la carrière 

Figure 19 : Relation entre la pluviométrie à SAINTES et les volumes pompés dans la carrière 

Figure 20 : Coupes géologiques transversales du projet d’extension 

Figure 21 : Évolution des rabattements en fonction de la distance 

Figure 22 : Planche photographique - Sources et ruisseau (février et avril 2013) 

Figure 23 : Gestion des eaux sur la carrière 

Figure 24 : Plan du site de l’état actuel 

Figure 25 : Localisation des zones de perceptions en vue éloignée 

Figure 26 : Photographies des perceptions visuelles actuelles du site - Vues éloignées 

Figure 27 : Pho


3.2.2.3 Ventilation Industrielle

3.2.2.4 Electricité

3.2.3 Locaux administratifs et sociaux

3.2.4 Zones extérieures

3.2.5 Principaux réseaux desservant le site 

3.2.5.1 Réseau de distribution d’eau potable 

3.2.5.2 Réseau d’évacuation des eaux pluviales 

3.2.5.3 Réseau d’évacuation des eaux usées 

3.2.5.4 Station de prétraitement des EU

3.2.6 Caractéristiques constructives 

3.2.7 Substances dangereuses utlisées 
3.3

3.3.1 Synoptique bovin

3.3.2 Synoptique porcin 

3.3.3 Synoptique ovin 
3.4

4 ETUDE D’IMPACTS 

4.1 Introduction
4.2

4.2.1 Le contexte géographique et socio-économique

4.2.1.1 Le contexte géographique

4.2.1.2 Le contexte topographique

4.2.1.3 Le contexte socio-économique 

4.2.2 L’environnement du site 

4.2.2.1 Les communes voisines

4.2.2.2 Occupation des sols

4.2.2.3 Visibilité du site 

4.2.2.4 Accès et Infrastructures

4.2.3 Climatologie et qualité de l’air 

4.2.3.1 Précipitations

4.2.3.2 Soleil et Températures 

4.2.3.3 Vents 

4.2.3.4 Qualité de 

 
2
2
Pressions
2
2
2
164B
I 
ETEN Environnement i n /om *7
0
405 •
j/le Mou nard 346
2
2
non spontanée
Limousin
Limousin
m« mm Am««A Im Am mm*Am «mm   m Amm «* m
«Am • m mA mm Am
Am«m«mm Jm
Limousin
Limousin
), l’Œdipode turquoise (
), Criquet ensanglanté (
 
1 orthoptère est considéré comme patrimonial : le Conocéphale des roseaux (
1 papillon de jour : l’Azuré de l’Ajonc (
1 espèce de libellule potentiellement présente, l’Agrion mignon ( 
1 espèce de libellule potentiellement présente, le Leste verdoyant ( 
3 espèces d’amphibiens ont été observées sur l’aire d’étude immédiate : la Grenouille verte (
 ).
4 espèces de reptiles ont été observées sur l’aire d’étude immédiate : Le Lézard des murailles ( 
37 espèces observées dont 29 espèces protégées
2
1
2
1
2
2
+ 
1
2
l’érosion hydrique.
2
2
2
4
5
2
2
(prairies, landes), des 
3
 en
pour l’EARL de Bellevue.
1
Compensation agricole
1
1
8
VmÀ
7
1
1
3
5
1
9
2
II. Effets
et les 
 Effet de la fauche sur la biodiversité :
CHAMBRE D'AGRICULTURE

In [265]:
vide=[i for i in np.unique(base_finale.num_etude) if base_finale[base_finale.num_etude==i].label_active.sum()==0]
len(vide)

20

In [230]:
train_active[train_active.num_etude==1098190][50:150]

phrase  num_etude                                           phrase_2         0  ventre_0  ventre_1  ventre_2  ventre_3  ventre_4  ventre_5  ventre_6  ventre_7  ventre_8  ventre_9  ventre_10  ventre_11   33   34   35   36   37   38   39    f_mots   f_carac  html_carac  ind_sommaire  sommaire_longueur  sommaire_int  caractere_spec  label_k_3  label_RF  label
508152  <li>\n<p><a href="#bookmark33"><span class="fo...    1098190                         \n2.6.2. Impacts positifs   0.046809  0.748300  0.000000  0.455861  0.130619  0.576965  0.889147  0.490925  0.277760  0.314441  0.323529   0.257970   0.234348  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.008523  0.010340    0.022509           0.0                0.0           0.0             0.0          1       0.0    0.0
508153  <li>\n<p><a href="#bookmark34"><span class="fo...    1098190               \n2.6.3. Impacts négatifs et mesures  0.046809  0.748300  0.000000  0.455861  0.130619  0.576965  0.889147  0.490925  0.277760  0.314441  0.323529   0.257970   0.234348  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.011364  0.014649    0.025254           0.0                0.0           0.0             0.0          1       0.0    0.0
508154  <li>\n<p><a href="#bookmark35"><span class="fo...    1098190  \n2.7. Incidences du projet sur le climat et v...  0.051064  0.400452  0.377514  0.834389  0.045256  0.607546  0.895715  0.468707  0.292211  0.451320  0.305309   0.168661   0.253249  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.039773  0.039638    0.048312           0.0                0.0           0.0             0.0          1       0.0    0.0
508155  <li>\n<p><a href="#bookmark36"><span class="fo...    1098190       \n2.7.1. Incidences du projet sur le climat   0.046809  0.748300  0.000000  0.455861  0.130619  0.576965  0.889147  0.490925  0.277760  0.314441  0.323529   0.257970   0.234348  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.019886  0.018096    0.027450           0.0                0.0           0.0             0.0          1       0.0    0.0
508156  <li>\n<p><a href="#bookmark37"><span class="fo...    1098190  \n2.7.2. Vulnérabilité du projet au changement...  0.046809  0.748300  0.000000  0.455861  0.130619  0.576965  0.889147  0.490925  0.277760  0.314441  0.323529   0.257970   0.234348  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.019886  0.024128    0.031293           0.0                0.0           0.0             0.0          1       0.0    0.0
508157  <li>\n<p><a href="#bookmark38"><span class="fo...    1098190  \n2.8. Incidences négatives notables du projet...  0.051064  0.400452  0.377514  0.834389  0.045256  0.607546  0.895715  0.468707  0.292211  0.451320  0.305309   0.168661   0.253249  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.065341  0.069798    0.067527           0.0                0.0           0.0             0.0          1       0.0    0.0
508158  <li>\n<p><a href="#bookmark39"><span class="fo...    1098190       \n2.9. Incidences sur les sites Natura 2000   0.051064  0.400452  0.377514  0.834389  0.045256  0.607546  0.895715  0.468707  0.292211  0.451320  0.305309   0.168661   0.253249  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.019886  0.018096    0.034587           0.0                0.0           0.0             0.0          1       0.0    0.0
508159  <li>\n<p><a href="#bookmark40"><span class="fo...    1098190  \n2.10. Compatibilité du projet avec les docum...  0.051064  0.400452  0.377514  0.834389  0.045256  0.607546  0.895715  0.468707  0.292211  0.451320  0.305309   0.168661   0.253249  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.022727  0.028005    0.040900           0.0                0.0           0.0             0.0          1       0.0    0.0
508160  <li>\n<p><a href="#bookmark41"><span class="fo...    1098190  \n2.11. Dispositifs de suivi et coût des mesur...  0.051064  0.400452  0.377514  0.834389  0.045256  0.607546  0.895715  0.468707  0.292211  0.451320  0.305309   0.168661   0.253249  0.0  0.0  0.0  0.0  0.0  0.0  0.0  0.034091  0.032745    0.043920           0.0                0.0          

In [224]:
vide
#112862
#196750
#1008101
#1078725
#1259375
#2072251 c'est un avis ???
#2255947

[112862,
 196750,
 229167,
 238301,
 1007765,
 1008101,
 1012199,
 1017145,
 1078725,
 1098190,
 1171621,
 1259375,
 1864915,
 1945141,
 2034810,
 2072251,
 2207085,
 2244404,
 2255947,
 2376874]

# 5. Analyse des titres non détectés (exploratoire, à ne pas faire tourner sauf exception)

Dans un premier temps, quantifions la quantité de documents n'ayant pas de titres détectés.

In [0]:
base_finale

In [0]:
vide=[i for i in np.unique(base_finale.num_etude) if base_finale[base_finale.num_etude==i].label_RF.sum()==0]

In [0]:
np.unique(base_finale.num_etude)[0]

In [0]:
non_vide=[i for i in np.unique(base_finale.num_etude) if i not in vide]
len(non_vide)/len(np.unique(base_finale.num_etude))

In [0]:
index_vide=[True if base_finale.num_etude[i] in vide else False for i in base_finale.index]
base_relou=base_finale[index_vide]
base_relou

In [0]:
print("Proportion des labels kmeans chez les vides,\nnon-titres (1) :",round(base_relou.label_k.sum()/len(base_relou)*100,2))
print("Proportion des labels kmeans chez les non vides,\nnon-titres (1) :",round(base_propre.label_k.sum()/len(base_propre)*100,2))
print("Proportion des labels kmeans total,\nnon-titres (1) :",round(base_finale.label_k.sum()/len(base_finale)*100,2))
numero=np.unique(base_relou.num_etude)
k=0
titres=list(base_relou[base_relou.label_k==1][base_relou.num_etude==numero[k]].phrase_2.values)
for i in titres:
    print('\nIndice :',titres.index(i),i)

In [0]:
numero=np.unique(base_relou.num_etude)
k=0
titres=list(base_relou[base_relou.ind_sommaire==1][base_relou.num_etude==numero[k]].phrase_2.values)
for i in titres:
    print('\nIndice :',titres.index(i),i)

In [0]:
base_relou[base_relou.ind_sommaire==1][base_relou.num_etude==numero[k]]

Problème sur le clustering Kmeans, probablement du à ind_sommaire ?

In [0]:
len(base_relou),len(base_finale)

In [0]:
index_nonvide=[bool(abs(i-1)) for i in index_vide]
base_propre=base_finale[index_nonvide]
distrib_nbligne_propre=[len(base_propre[base_propre.num_etude==i]) for i in np.unique(base_propre.num_etude)]
print("Pourcentage d'études vides :",round(len(non_vide)/len(np.unique(base_finale.num_etude))*100,2),"%")
print('Les documents vides représentent',round(len(base_relou)/len(base_finale)*100,2),'% de la base pour la classification supervisée')

In [0]:
numero=np.unique(base_propre.num_etude)
k=8
titres=list(base_propre[base_propre.label_k==1][base_propre.num_etude==numero[k]].phrase_2.values)
for i in titres:
    print('\nIndice :',titres.index(i),i)

In [0]:
distrib_nbligne_vide=[len(base_relou[base_relou.num_etude==i]) for i in np.unique(base_relou.num_etude)]

In [0]:
def stat_des(x,mo,k=2):
    if mo=='mean':
        y=np.mean(x)
    elif mo=='std':
        y=np.std(x)
    elif mo=='med':
        y=np.median(x)
    else:
        raise ValueError('Veuillez spécifier quel type de stat des vous voulez. Valeurs possibles : mean, std ou med')
    z=round(y,k)
    return z

print("Pour les documents non vides, distribution du nombre de lignes html, \nmoyenne :",stat_des(distrib_nbligne_propre,'mean'),"\nécart-type :",stat_des(distrib_nbligne_propre,'std'),'\nmédiane :',stat_des(distrib_nbligne_propre,'med'))
print("Pour les documents vides, distribution du nombre de lignes html, \nmoyenne :",stat_des(distrib_nbligne_vide,'mean'),"\nécart-type :",stat_des(distrib_nbligne_vide,'std'),'\nmédiane :',stat_des(distrib_nbligne_vide,'med'))

In [0]:
import matplotlib.pyplot as plt
figue,hache=plt.subplots(figsize=(18,12))
#sns.kdeplot(distrib_nbligne_propre , bw = 0.5 , fill = True)
#sns.kdeplot(distrib_nbligne_vide , bw = 0.5 , fill = True)
sns.distplot(distrib_nbligne_propre)
sns.distplot(distrib_nbligne_vide)

#hache.hist(distrib_nbligne_propre,density=True,bins=20)
#hache.hist(distrib_nbligne_vide,density=True,bins=20)
plt.legend(['propre','vide'])

Maintenant qu'on a analysé le problème et trouvé une source de problème, on repasse la base_relou à la moulinette pour voir si ça s'arrange

In [0]:
def sommaire(s):
    '''
    Fonction cherchant l'indice du début du sommaire dans la liste de phrase.
    '''
    somm=['SOMMAIRE','sommaire','Sommaire']
    s=list(s)
    indice=[s.index(k) for k in somm if k in s]
    if len(indice)==0:
        indice=[i for i in range(len(s)) if np.sum([1 if som in s[i] else 0 for som in somm])>0]
        if len(indice)>2:
            indice=[indice[0]]
        if len(indice)==0:
            from unidecode import unidecode
            technique=[unidecode('table des matières'.lower()),'non technique']
            indice=[i for i in range(len(s)) if np.sum([1 if som in unidecode(s[i].lower()) else 0 for som in technique])>0]
    #[list(verif_theo[verif_theo.label_k==0][verif_theo.num_etude==verif_theo.num_etude[0]].phrase_2.values).index(k) for k in somm if k in list(verif_theo[verif_theo.label_k==0][verif_theo.num_etude==verif_theo.num_etude[0]].phrase_2.values)]
    return indice

def light_cleaning(s):
    import re
    from unidecode import unidecode
    import numpy as np
    s=unidecode(s)
    s=re.sub(r'[^A-Za-z]',' ',s)
    s=s.lower()
    s=s.split(' ')
    s=list(np.unique(s))
    try:
        s.remove('')
        return s
    except:
        return s


def indice_relou(liste,indice_sommaire,seuil,seuil_c):
    '''
    Fonction qui permet de produire l'indicatrice sommaire pour les études récalcitrantes : c'est-à-dire dont le sommaire est difficilement détectable.
    Par exemple à cause de mauvaises répétitions des titres, d'absence de mots indiquants le début ou la fin du sommaire etc...
    '''
    import re
    output=None
    x=0
    #if procede=='basic':
    while output is None:
        x+=1
        a=light_cleaning(liste[indice_sommaire[0]+x])
        for j in range(indice_sommaire[0]+1+1,len(liste)):
            b=light_cleaning(liste[j])
            cnt = 0
            if len(a)==1:
                s=0
                for i in a:
                    if type(b)==str:
                        if re.search(i, b) is not None:
                            cnt = cnt + 1
                cnt=cnt/len(a)
                count=len(set(a)&set(b))/len(a)
            elif len(a)>1:
                aa=''.join([i for i in a])
                for i in aa:
                    if type(b)==str:
                        if re.search(i, b) is not None:
                            cnt = cnt + 1
                cnt=cnt/len(aa)
                count=len(set(aa)&set(b))/len(aa)
                s=0
                if type(b)==str:
                    for i in b:
                        if i in a:
                            s=1

            if (b in a) or (a in b) or (cnt>seuil) or (count>seuil_c) or (s>0):
                output=j
                #vector=np.ones(len([indice_sommaire[0]:j]))
                break
            else:
                continue
  #  elif procede=='further':
   #     a=light_cleaning(liste[indice_sommaire[0]])
    #else:
       # raise ValueError("Hum... Êtes-vous sûr que vous avez correctement spécifié le variable procede ? \nLes valeurs possibles sont 'basic' et 'further' (pour les études récalcitrantes).")

    return output

def ind_titres(verif,brutal=None,seuil_sommaire=50,seuil=0.35,seuil_c=0.35):
    verif_theo=verif.copy()
    titres={}
    vector_=[]
    indexes = np.unique(verif_theo.num_etude, return_index=True)[1]
    print(indexes)
    try:
        interval=[verif_theo.num_etude[index] for index in sorted(indexes)]
    except:
        verif_theo=verif_theo.reset_index(drop=True)
        interval=[verif_theo.num_etude[index] for index in sorted(indexes)]
    print(interval)
    h=0
    for i in interval:
        print("On étudie l'étude :",i)
        liste=verif_theo[verif_theo.num_etude==i].phrase_2.values
        vector=np.zeros(len(liste))
        vector_.append(vector)
        h=h+len(vector)
        #vector_.append(vector)
        indice_sommaire=sommaire(liste)
        if len(indice_sommaire)>0:
            a=light_cleaning(liste[indice_sommaire[0]+1]) #hypothèse donc que le 1er titre vient après le sommaire
            print("L'indice de début de sommaire pour l'étude",i,"est",indice_sommaire[0],a)
            for j in range(indice_sommaire[0]+1+1,len(liste)):
                b=light_cleaning(liste[j])
                if a==b:
                    vector_[interval.index(i)][indice_sommaire[0]:j]=1
                    break
                else:
                    continue
            if np.sum(vector_[interval.index(i)])>0:
                print("Il y a un sommaire pour l'étude :",i)
            elif np.sum(vector_[interval.index(i)])==0:
                print('On tente la nouvelle méthode')
                j=indice_relou(liste,indice_sommaire,seuil,seuil_c)
                if j is not None:
                    vector_[interval.index(i)][indice_sommaire[0]:j]=np.ones(len(range(indice_sommaire[0],j)))
                    ss=np.sum(vector_[interval.index(i)])
                    if ss>seuil_sommaire:
                        print("Il y a un sommaire pour l'étude :",i)
                    elif (ss>0) and (ss<seuil_sommaire) and (brutal is not None):
                        print("Hum... Le sommaire semble petit :",ss)
                        vector_[interval.index(i)][indice_sommaire[0]:brutal]=np.ones(len(range(indice_sommaire[0],brutal)))
                    else:
                        print("Pas de sommaire pour l'étude :",i)
                else:
                    print("Pour l'étude",i,"on n'a pas trouvé d'indice pour débuter le sommaire.")
        else:
            print("Pas de sommaire pour l'étude :",i)
    return vector_

In [0]:
technique=['non technique',unidecode('Table des matières'.lower())]
numero=np.unique(base_relou.num_etude)
indice=[i for i in range(len(base_relou[base_relou.num_etude==numero[3]].phrase_2.values))
        if np.sum([1 if som in unidecode(base_relou[base_relou.num_etude==numero[3]].phrase_2.values[i].lower()) else 0 for som in technique])>0]

In [0]:
numero=np.unique(base_relou.num_etude)
print("Il y a ",len(numero),"études vides")
k=8

titres=list(base_relou[base_relou.ind_sommaire==1][base_relou.num_etude==numero[k]].phrase_2.values)
for i in titres:
    print('\nIndice :',titres.index(i),"\n",i)

In [0]:
numero=np.unique(base_relou.num_etude)
index=[i for i in numero if np.sum(base_relou[base_relou.num_etude==i].ind_sommaire)==0]
base_relou_2=base_relou[[True if base_relou.num_etude[i] in index else False for i in base_relou.index]]
print("Les documents vides tenaces représentent :",round(len(base_relou_2)/len(base_relou)*100,2),'% des lignes de la base relou')
print("On a réussi à traiter ",round((1-len(np.unique(base_relou_2.num_etude))/len(numero))*100,2),"% des documents vides initiaux")
print("Il y a ",len(np.unique(base_relou_2.num_etude)),"études vides")

In [0]:
numero_2=np.unique(base_relou_2.num_etude)
k=0

titres=list(base_relou_2[base_relou_2.label_k==0][base_relou_2.num_etude==112862].phrase_2.values)
for i in titres:
    print('\nIndice :',titres.index(i),"\n",i)

In [0]:
liste=base_relou_2[base_relou_2.label_k==1][base_relou_2.num_etude==101872].phrase_2.values
s=sommaire(liste)
print(s)
#ind_titres(base_relou_2)
a=light_cleaning(liste[s[0]+1]) #hypothèse donc que le 1er titre vient après le sommaire
print(a)
print(''.join([i for i in a]))
j=indice_relou(liste,s,0.4,0.4)
j

In [0]:
ouais=ind_titres(base_relou_2)
c=functools.reduce(
    operator.iconcat,ouais,[])
print(len(c))
base_relou_2['ind_sommaire']=c

In [0]:
numero=np.unique(base_relou_2.num_etude)
print("Il y a ",len(numero),"études vides")
k=9

titres=list(base_relou_2[base_relou_2.ind_sommaire==1][base_relou_2.num_etude==numero[k]].phrase_2.values)
for i in titres:
    print('\nIndice :',titres.index(i),"\n",i)

In [0]:
numero=np.unique(base_relou_2.num_etude)
index=[i for i in numero if np.sum(base_relou_2[base_relou_2.num_etude==i].ind_sommaire)==0]
base_relou_3=base_relou_2[[True if base_relou_2.num_etude[i] in index else False for i in base_relou_2.index]]
print("Les documents vides tenaces représentent :",round(len(base_relou_3)/len(base_relou_2)*100,2),'% des lignes de la base relou')
print("On a réussi à traiter ",round((1-len(np.unique(base_relou_3.num_etude))/len(numero))*100,2),"% des documents vides initiaux")
print("Il y a ",len(np.unique(base_relou_3.num_etude)),"études vides")

In [0]:
def raffinement_sommaire(base_3,a,b):
    base=base_3.copy()
    c=[1 if len(i)>a or len(i)<b else 0 for i in base.phrase_2]#np.zeros(len(base))
    c_=np.zeros(len(base))
    for i in range(len(base)):
        try:
            k=int(base.phrase_2[i])
            #print(k)
            c_[i]=1
        except:
            continue
    base['sommaire_longueur']=c
    base['sommaire_int']=c_
    return base
base_=raffinement_sommaire(base_relou,180,3)
base_.sommaire_int=base_.sommaire_int*base_.ind_sommaire
base_.sommaire_longueur=base_.sommaire_longueur*base_.ind_sommaire
base_

In [0]:
base_.iloc[:,3:]

In [0]:
import pickle
da=dataiku.Folder('lZ0B3sSL')
kmeans=pickle.load(open(da.get_path()+"/kmeans_model.pickle",'rb'))
label_k_relou=kmeans.predict(base_.iloc[:,3:-2])
base_['label_k']=label_k_relou

In [0]:
label_RF_relou=Bagging.predict(base_.iloc[:,3:-1])
base_['label_RF']=label_RF_relou

In [0]:
numero=np.unique(base_.num_etude)
k=2
titres=list(base_[base_.label_RF==1][base_.num_etude==numero[k]].phrase_2.values)
for i in titres:
    print('\nIndice :',titres.index(i),i)

In [0]:
import seaborn as sns
sns.histplot(distrib_nbligne_propre,stat='frequency',bins=100)